# Classic NN

In [90]:
#scikit learn ensembe workflow for binary probability
import sys
sys.path.insert(0, "/opt/DL/tensorflow/lib/python2.7/site-packages/")
import time; start_time = time.time()
import numpy as np
import pandas as pd
from sklearn import ensemble
from sklearn.metrics import log_loss, make_scorer
import random; random.seed(7)
from math import*
from decimal import Decimal
import os
from scipy import fftpack
import csv
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.wrappers.scikit_learn import KerasClassifier
# from keras.utils import np_utils
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.preprocessing import LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from keras.optimizers import SGD
from keras.constraints import maxnorm
from keras.callbacks import ModelCheckpoint, Callback, EarlyStopping
from sklearn.preprocessing import StandardScaler
from sklearn.cross_validation import train_test_split

## Metrics definition

In [2]:
def histogram_intersection(h1, h2, bins):
   bins = np.diff(bins)
   sm = 0
   for i in range(len(bins)):
       sm += min(bins[i]*h1[i], bins[i]*h2[i])
   return sm

def manhattan_distance(x,y):
    return sum(abs(a-b) for a,b in zip(x,y))
 
def nth_root(value, n_root):
    root_value = 1/float(n_root)
    return round (Decimal(value) ** Decimal(root_value),3)
 
def minkowski_distance(x,y,p_value):
     return nth_root(sum(pow(abs(a-b),p_value) for a,b in zip(x, y)),p_value)
    
def square_rooted(x):
    return round(sqrt(sum([a*a for a in x])),3)
 
def cosine_similarity(x,y):
    numerator = sum(a*b for a,b in zip(x,y))
    denominator = square_rooted(x)*square_rooted(y)
    return round(numerator/float(denominator),3)    

def jaccard_similarity(x,y):
    intersection_cardinality = len(set.intersection(*[set(x), set(y)]))
    union_cardinality = len(set.union(*[set(x), set(y)]))
    return intersection_cardinality/float(union_cardinality)

def fft(img):
    # Take the fourier transform of the image.
    F1 = fftpack.fft2(img)
 
    # Now shift the quadrants around so that low spatial frequencies are in
    # the center of the 2D fourier transformed image.
    F2 = fftpack.fftshift( F1 )
 
    # Calculate a 2D power spectrum
    psd2D = np.abs( F2 )**2
    return psd2D

## Load original datasets

In [31]:
#Load data
train = pd.read_json("./train.json")
test = pd.read_json("./test.json")

In [34]:
train.head(5)
# test.head(5)

band_1  \
0  [-27.878361, -27.15416, -28.668615, -29.537971...   
1  [-12.242375, -14.920305, -14.920363, -12.66633...   
2  [-24.603676, -24.603714, -24.871029, -23.15277...   
3  [-22.454607, -23.082819, -23.998013, -23.99805...   
4  [-26.006956, -23.164886, -23.164886, -26.89116...   

                                              band_2        id inc_angle  \
0  [-27.154118, -29.537888, -31.0306, -32.190483,...  dfd5f913   43.9239   
1  [-31.506321, -27.984554, -26.645678, -23.76760...  e25388fd   38.1562   
2  [-24.870956, -24.092632, -20.653963, -19.41104...  58b2aaa0   45.2859   
3  [-27.889421, -27.519794, -27.165262, -29.10350...  4cfc3a18   43.8306   
4  [-27.206915, -30.259186, -30.259186, -23.16495...  271f93f4   35.6256   

   is_iceberg  
0           0  
1           0  
2           1  
3           0  
4           0

## Compute train and test metrics

In [4]:
# Train data
metrics = []

if os.path.isfile('./train_metrics.csv'):
    print 'Already done...'
else:
    for idx in range(0,train.shape[0]):
        row = []
        img1 = train.loc[idx, ['band_1', 'band_2']]
        target = (train.loc[idx, ['is_iceberg']])[0]
        row.append(target)
        
        id = (train.loc[idx, ['id']])[0]
        row.append(id)

        img1 = np.stack([img1['band_1'], img1['band_2']], -1).reshape(75, 75, 2)
        band1 = img1[:, :, 0]
        band1 = (band1 + abs(band1.min())) / np.max((band1 + abs(band1.min())))

        band2 = img1[:, :, 1]
        band2 = (band2 + abs(band2.min())) / np.max(band2 + abs(band2.min()))

        fft_band1 = fft(band1)
        fft_band2 = fft(band2)

        hband1, hbins = np.histogram(band1, bins=256, normed=True)
        hband2, hbins = np.histogram(band2, bins=256, normed=True)

        fft_hband1, hbins = np.histogram(fft_band1, bins=256, normed=True)
        fft_hband2, hbins = np.histogram(fft_band2, bins=256, normed=True)

        hist_band1 = np.array([hband1]).ravel()
        series_band1 = pd.Series(hist_band1)
        hist_band2 = np.array([hband2]).ravel()
        series_band2 = pd.Series(hist_band2)

        fft_hist_band1 = np.array([fft_hband1]).ravel()
        fft_series_band1 = pd.Series(fft_hist_band1)
        fft_hist_band2 = np.array([fft_hband2]).ravel()
        fft_series_band2 = pd.Series(fft_hist_band2)

        diff = series_band1 - series_band2
        distance = np.sqrt(np.dot(diff, diff))
        row.append(distance)

        inter = histogram_intersection(hband1, hband2, hbins)
        row.append(inter)

        diff = fft_series_band1 - fft_series_band2
        distance = np.sqrt(np.dot(diff, diff))
        row.append(distance)

        inter = histogram_intersection(fft_hband1, fft_hband2, hbins)
        row.append(inter)

        manhattan = manhattan_distance(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(manhattan)

        minkowski = minkowski_distance(np.array([band1]).ravel(),np.array([band2]).ravel(), 3)
        row.append(minkowski)

        cos_simil = cosine_similarity(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(cos_simil)

        jaccard_simil = jaccard_similarity(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(jaccard_simil)
        
        metrics.append(row)

    header = 'target', 'id', 'normal_dist','normal_intersec', 'fft_dist','fft_intersec', 'manhattan_dist', 'minkowski_dist', 'cosine_simil', 'jaccard_simil'
            
    with open("./train_metrics.csv", "wb") as f:
        writer = csv.writer(f)
        writer.writerow(header)
        writer.writerows(metrics)

Already done...


In [60]:
# Test data
metrics = []

# print test.shape[0]

if os.path.isfile('./test_metrics.csv'):
    print 'Already done...'
else:
    for idx in range(0,test.shape[0]):
        row = []
        img1 = test.loc[idx, ['band_1', 'band_2']]
        
        row.append(0)
        
        id = (test.loc[idx, ['id']])[0]
        row.append(id)
        
        img1 = np.stack([img1['band_1'], img1['band_2']], -1).reshape(75, 75, 2)
        band1 = img1[:, :, 0]
        band1 = (band1 + abs(band1.min())) / np.max((band1 + abs(band1.min())))

        band2 = img1[:, :, 1]
        band2 = (band2 + abs(band2.min())) / np.max(band2 + abs(band2.min()))

        fft_band1 = fft(band1)
        fft_band2 = fft(band2)

        hband1, hbins = np.histogram(band1, bins=256, normed=True)
        hband2, hbins = np.histogram(band2, bins=256, normed=True)

        fft_hband1, hbins = np.histogram(fft_band1, bins=256, normed=True)
        fft_hband2, hbins = np.histogram(fft_band2, bins=256, normed=True)

        hist_band1 = np.array([hband1]).ravel()
        series_band1 = pd.Series(hist_band1)
        hist_band2 = np.array([hband2]).ravel()
        series_band2 = pd.Series(hist_band2)

        fft_hist_band1 = np.array([fft_hband1]).ravel()
        fft_series_band1 = pd.Series(fft_hist_band1)
        fft_hist_band2 = np.array([fft_hband2]).ravel()
        fft_series_band2 = pd.Series(fft_hist_band2)

        diff = series_band1 - series_band2
        distance = np.sqrt(np.dot(diff, diff))
        row.append(distance)

        inter = histogram_intersection(hband1, hband2, hbins)
        row.append(inter)

        diff = fft_series_band1 - fft_series_band2
        distance = np.sqrt(np.dot(diff, diff))
        row.append(distance)

        inter = histogram_intersection(fft_hband1, fft_hband2, hbins)
        row.append(inter)

        manhattan = manhattan_distance(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(manhattan)

        minkowski = minkowski_distance(np.array([band1]).ravel(),np.array([band2]).ravel(), 3)
        row.append(minkowski)

        cos_simil = cosine_similarity(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(cos_simil)

        jaccard_simil = jaccard_similarity(np.array([band1]).ravel(),np.array([band2]).ravel())
        row.append(jaccard_simil)
        
        metrics.append(row)

    header = 'target', 'id', 'normal_dist','normal_intersec', 'fft_dist','fft_intersec', 'manhattan_dist', 'minkowski_dist', 'cosine_simil', 'jaccard_simil'
            
    with open("./test_metrics.csv", "wb") as f:
        writer = csv.writer(f)
        writer.writerow(header)
        writer.writerows(metrics)

8424


# Classic NN

## load metrics

In [35]:
train = pd.read_csv('./train_metrics.csv')
# test = pd.read_csv('./test_metrics.csv')
# num_train = train.shape[0]
train.head(5)

target        id  normal_dist  normal_intersec  fft_dist  fft_intersec  \
0       0  dfd5f913    76.651440     6.723106e+05  0.000053           1.0   
1       0  e25388fd    34.406942     1.163699e+06  0.000002           1.0   
2       1  58b2aaa0    53.654686     2.018744e+06  0.000010           1.0   
3       0  4cfc3a18    61.308585     7.313449e+05  0.000043           1.0   
4       0  271f93f4    58.743545     1.380521e+06  0.000031           1.0   

   manhattan_dist  minkowski_dist  cosine_simil  jaccard_simil  
0      665.890895           2.821         0.957       0.000582  
1      384.697248           1.809         0.953       0.000314  
2      721.904482           3.317         0.954       0.000423  
3      448.786755           2.041         0.952       0.000488  
4      784.238485           3.330         0.965       0.000435

In [40]:
# Normalize the columns
cols_to_norm = ['normal_dist','normal_intersec', 'fft_dist', 'fft_intersec', 'manhattan_dist', 'minkowski_dist', 'cosine_simil', 'jaccard_simil']
train[cols_to_norm] = train[cols_to_norm].apply(lambda x: (x - x.min()) / (x.max() - x.min()))
train.head(5)

target        id  normal_dist  normal_intersec  fft_dist  fft_intersec  \
0       0  dfd5f913     0.713580         0.152752  0.344405           1.0   
1       0  e25388fd     0.194141         0.271464  0.012653           1.0   
2       1  58b2aaa0     0.430811         0.478030  0.062200           1.0   
3       0  4cfc3a18     0.524924         0.167014  0.282412           1.0   
4       0  271f93f4     0.493384         0.323845  0.204589           1.0   

   manhattan_dist  minkowski_dist  cosine_simil  jaccard_simil  
0        0.229014        0.274443      0.629032       0.637750  
1        0.074739        0.109810      0.564516       0.109803  
2        0.259746        0.355133      0.580645       0.324363  
3        0.109901        0.147552      0.548387       0.452659  
4        0.293945        0.357247      0.758065       0.347645

## build datasets

In [5]:
dataset = train.values
X = dataset[:,2:10].astype(float)
y = dataset[:,0]


## very simple model :-)

In [15]:
# define baseline model
def baseline_model():
    # create model
    model = Sequential()
    model.add(Dense(16, input_dim=8, activation='relu'))
    model.add(Dense(2, activation='softmax'))
    # Compile model
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

In [16]:
seed = 7
np.random.seed(seed)

estimator = KerasClassifier(build_fn=baseline_model, epochs=200, batch_size=5, verbose=2)
kfold = KFold(n_splits=3, shuffle=True, random_state=seed)

In [17]:
results = cross_val_score(estimator, X, y, cv=kfold)
print("Baseline: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Epoch 1/200
 - 1s - loss: 0.6812 - acc: 0.5650
Epoch 2/200
 - 1s - loss: 0.6745 - acc: 0.5753
Epoch 3/200
 - 1s - loss: 0.6658 - acc: 0.5921
Epoch 4/200
 - 1s - loss: 0.6639 - acc: 0.6043
Epoch 5/200
 - 1s - loss: 0.6574 - acc: 0.6015
Epoch 6/200
 - 1s - loss: 0.6529 - acc: 0.6062
Epoch 7/200
 - 1s - loss: 0.6491 - acc: 0.6080
Epoch 8/200
 - 1s - loss: 0.6465 - acc: 0.6127
Epoch 9/200
 - 1s - loss: 0.6428 - acc: 0.6202
Epoch 10/200
 - 1s - loss: 0.6393 - acc: 0.6090
Epoch 11/200
 - 1s - loss: 0.6362 - acc: 0.6239
Epoch 12/200
 - 1s - loss: 0.6332 - acc: 0.6258
Epoch 13/200
 - 1s - loss: 0.6318 - acc: 0.6361
Epoch 14/200
 - 1s - loss: 0.6262 - acc: 0.6342
Epoch 15/200
 - 1s - loss: 0.6279 - acc: 0.6361
Epoch 16/200
 - 1s - loss: 0.6198 - acc: 0.6361
Epoch 17/200
 - 1s - loss: 0.6190 - acc: 0.6492
Epoch 18/200
 - 1s - loss: 0.6147 - acc: 0.6492
Epoch 19/200
 - 1s - loss: 0.6096 - acc: 0.6464
Epoch 20/200
 - 1s - loss: 0.6096 - acc: 0.6558
Epoch 21/200
 - 1s - loss: 0.6031 - acc: 0.6660
E

Epoch 171/200
 - 1s - loss: 0.4983 - acc: 0.7428
Epoch 172/200
 - 1s - loss: 0.4990 - acc: 0.7558
Epoch 173/200
 - 1s - loss: 0.4942 - acc: 0.7446
Epoch 174/200
 - 1s - loss: 0.4987 - acc: 0.7399
Epoch 175/200
 - 1s - loss: 0.4981 - acc: 0.7530
Epoch 176/200
 - 1s - loss: 0.5021 - acc: 0.7287
Epoch 177/200
 - 1s - loss: 0.4997 - acc: 0.7409
Epoch 178/200
 - 1s - loss: 0.4991 - acc: 0.7418
Epoch 179/200
 - 1s - loss: 0.5022 - acc: 0.7325
Epoch 180/200
 - 1s - loss: 0.4988 - acc: 0.7371
Epoch 181/200
 - 1s - loss: 0.5008 - acc: 0.7437
Epoch 182/200
 - 1s - loss: 0.4986 - acc: 0.7381
Epoch 183/200
 - 1s - loss: 0.4991 - acc: 0.7437
Epoch 184/200
 - 1s - loss: 0.5006 - acc: 0.7371
Epoch 185/200
 - 1s - loss: 0.4982 - acc: 0.7399
Epoch 186/200
 - 1s - loss: 0.5005 - acc: 0.7418
Epoch 187/200
 - 1s - loss: 0.5021 - acc: 0.7362
Epoch 188/200
 - 1s - loss: 0.4968 - acc: 0.7474
Epoch 189/200
 - 1s - loss: 0.4985 - acc: 0.7446
Epoch 190/200
 - 1s - loss: 0.4982 - acc: 0.7474
Epoch 191/200
 - 1s 

Epoch 141/200
 - 1s - loss: 0.4991 - acc: 0.7390
Epoch 142/200
 - 1s - loss: 0.4985 - acc: 0.7343
Epoch 143/200
 - 1s - loss: 0.5001 - acc: 0.7353
Epoch 144/200
 - 1s - loss: 0.5011 - acc: 0.7362
Epoch 145/200
 - 1s - loss: 0.5006 - acc: 0.7371
Epoch 146/200
 - 1s - loss: 0.5002 - acc: 0.7325
Epoch 147/200
 - 1s - loss: 0.4997 - acc: 0.7381
Epoch 148/200
 - 1s - loss: 0.5004 - acc: 0.7371
Epoch 149/200
 - 1s - loss: 0.4979 - acc: 0.7381
Epoch 150/200
 - 1s - loss: 0.5000 - acc: 0.7399
Epoch 151/200
 - 1s - loss: 0.4968 - acc: 0.7418
Epoch 152/200
 - 1s - loss: 0.4990 - acc: 0.7381
Epoch 153/200
 - 1s - loss: 0.4995 - acc: 0.7306
Epoch 154/200
 - 1s - loss: 0.4991 - acc: 0.7315
Epoch 155/200
 - 1s - loss: 0.4995 - acc: 0.7353
Epoch 156/200
 - 1s - loss: 0.5001 - acc: 0.7428
Epoch 157/200
 - 1s - loss: 0.4988 - acc: 0.7297
Epoch 158/200
 - 1s - loss: 0.4970 - acc: 0.7446
Epoch 159/200
 - 1s - loss: 0.5006 - acc: 0.7428
Epoch 160/200
 - 1s - loss: 0.4971 - acc: 0.7428
Epoch 161/200
 - 1s 

Epoch 111/200
 - 1s - loss: 0.5082 - acc: 0.7355
Epoch 112/200
 - 1s - loss: 0.5113 - acc: 0.7402
Epoch 113/200
 - 1s - loss: 0.5102 - acc: 0.7402
Epoch 114/200
 - 1s - loss: 0.5105 - acc: 0.7374
Epoch 115/200
 - 1s - loss: 0.5100 - acc: 0.7346
Epoch 116/200
 - 1s - loss: 0.5104 - acc: 0.7439
Epoch 117/200
 - 1s - loss: 0.5093 - acc: 0.7364
Epoch 118/200
 - 1s - loss: 0.5060 - acc: 0.7439
Epoch 119/200
 - 1s - loss: 0.5091 - acc: 0.7449
Epoch 120/200
 - 1s - loss: 0.5096 - acc: 0.7430
Epoch 121/200
 - 1s - loss: 0.5060 - acc: 0.7383
Epoch 122/200
 - 1s - loss: 0.5090 - acc: 0.7439
Epoch 123/200
 - 1s - loss: 0.5079 - acc: 0.7383
Epoch 124/200
 - 1s - loss: 0.5080 - acc: 0.7374
Epoch 125/200
 - 1s - loss: 0.5066 - acc: 0.7439
Epoch 126/200
 - 1s - loss: 0.5082 - acc: 0.7430
Epoch 127/200
 - 1s - loss: 0.5078 - acc: 0.7355
Epoch 128/200
 - 1s - loss: 0.5083 - acc: 0.7421
Epoch 129/200
 - 1s - loss: 0.5079 - acc: 0.7402
Epoch 130/200
 - 1s - loss: 0.5077 - acc: 0.7364
Epoch 131/200
 - 1s 

##  Larger model using gridsearch

### Tune  # of epochs and batch size 

In [17]:
# Function to create model, required for KerasClassifier
def create_model():
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer='normal', activation='relu'))
    model.add(Dense(30, kernel_initializer='normal', activation='relu'))
    model.add(Dense(1, kernel_initializer='normal', activation='sigmoid'))
    # Compile model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model
# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, verbose=1)
# define the grid search parameters
batch_size = [10, 20, 40, 60, 80, 100]
epochs = [10, 50, 100]
param_grid = dict(batch_size=batch_size, epochs=epochs)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/10
1069/1069 [==============================] - 2s 2ms/step - loss: 0.6909 - acc: 0.5557
Epoch 2/10
1069/1069 [==============================] - 0s 165us/step - loss: 0.6871 - acc: 0.5575
Epoch 3/10
1069/1069 [==============================] - 0s 164us/step - loss: 0.6836 - acc: 0.5575
Epoch 4/10
1069/1069 [==============================] - 0s 170us/step - loss: 0.6768 - acc: 0.5594
Epoch 5/10
1069/1069 [==============================] - 0s 171us/step - loss: 0.6638 - acc: 0.5762
Epoch 6/10
1069/1069 [==============================] - 0s 171us/step - loss: 0.6411 - acc: 0.5912
Epoch 7/10
1069/1069 [==============================] - 0s 160us/step - loss: 0.6223 - acc: 0.6286
Epoch 8/10
1069/1069 [==============================] - 0s 166us/step - loss: 0.6026 - acc: 0.6511
Epoch 9/10
1069/1069 [==============================] - 0s 164us/step - loss: 0.5890 - acc: 0.6473
Epoch 10/10
1069/1069 [==============================] - 0s 89us/step
Epoch 1/10
1069/1069 [===================

Epoch 50/50
1069/1069 [==============================] - 0s 93us/step
Epoch 1/50
1069/1069 [==============================] - 3s 2ms/step - loss: 0.6915 - acc: 0.5463
Epoch 2/50
1069/1069 [==============================] - 0s 170us/step - loss: 0.6886 - acc: 0.5463
Epoch 3/50
1069/1069 [==============================] - 0s 172us/step - loss: 0.6850 - acc: 0.5463
Epoch 4/50
1069/1069 [==============================] - 0s 172us/step - loss: 0.6748 - acc: 0.5463
Epoch 5/50
1069/1069 [==============================] - 0s 171us/step - loss: 0.6621 - acc: 0.5463
Epoch 6/50
1069/1069 [==============================] - 0s 171us/step - loss: 0.6332 - acc: 0.5463
Epoch 7/50
1069/1069 [==============================] - 0s 170us/step - loss: 0.6126 - acc: 0.6090
Epoch 8/50
1069/1069 [==============================] - 0s 172us/step - loss: 0.6014 - acc: 0.6492
Epoch 9/50
1069/1069 [==============================] - 0s 167us/step - loss: 0.5852 - acc: 0.6642
Epoch 10/50
1069/1069 [==================

1069/1069 [==============================] - 0s 175us/step - loss: 0.5159 - acc: 0.7072
Epoch 60/100
1069/1069 [==============================] - 0s 178us/step - loss: 0.5229 - acc: 0.7100
Epoch 61/100
1069/1069 [==============================] - 0s 177us/step - loss: 0.5186 - acc: 0.7138
Epoch 62/100
1069/1069 [==============================] - 0s 158us/step - loss: 0.5177 - acc: 0.7109
Epoch 63/100
1069/1069 [==============================] - 0s 158us/step - loss: 0.5193 - acc: 0.7100
Epoch 64/100
1069/1069 [==============================] - 0s 159us/step - loss: 0.5184 - acc: 0.7147
Epoch 65/100
1069/1069 [==============================] - 0s 167us/step - loss: 0.5176 - acc: 0.7063
Epoch 66/100
1069/1069 [==============================] - 0s 157us/step - loss: 0.5192 - acc: 0.7147
Epoch 67/100
1069/1069 [==============================] - 0s 158us/step - loss: 0.5218 - acc: 0.7109
Epoch 68/100
1069/1069 [==============================] - 0s 164us/step - loss: 0.5141 - acc: 0.7156
Epo

1070/1070 [==============================] - 0s 179us/step - loss: 0.5328 - acc: 0.7224
Epoch 20/100
1070/1070 [==============================] - 0s 179us/step - loss: 0.5323 - acc: 0.7355
Epoch 21/100
1070/1070 [==============================] - 0s 178us/step - loss: 0.5307 - acc: 0.7308
Epoch 22/100
1070/1070 [==============================] - 0s 179us/step - loss: 0.5311 - acc: 0.7308
Epoch 23/100
1070/1070 [==============================] - 0s 182us/step - loss: 0.5328 - acc: 0.7336
Epoch 24/100
1070/1070 [==============================] - 0s 174us/step - loss: 0.5299 - acc: 0.7336
Epoch 25/100
1070/1070 [==============================] - 0s 180us/step - loss: 0.5258 - acc: 0.7364
Epoch 26/100
1070/1070 [==============================] - 0s 177us/step - loss: 0.5329 - acc: 0.7234
Epoch 27/100
1070/1070 [==============================] - 0s 179us/step - loss: 0.5237 - acc: 0.7421
Epoch 28/100
1070/1070 [==============================] - 0s 175us/step - loss: 0.5251 - acc: 0.7336
Epo

1069/1069 [==============================] - ETA: 0s - loss: 0.5252 - acc: 0.713 - 0s 90us/step - loss: 0.5338 - acc: 0.6969
Epoch 49/50
1069/1069 [==============================] - 0s 91us/step - loss: 0.5306 - acc: 0.7044
Epoch 50/50
1069/1069 [==============================] - 0s 54us/step
Epoch 1/50
1069/1069 [==============================] - 3s 3ms/step - loss: 0.6920 - acc: 0.5398
Epoch 2/50
1069/1069 [==============================] - 0s 87us/step - loss: 0.6897 - acc: 0.5463
Epoch 3/50
1069/1069 [==============================] - 0s 85us/step - loss: 0.6878 - acc: 0.5463
Epoch 4/50
1069/1069 [==============================] - 0s 88us/step - loss: 0.6857 - acc: 0.5463
Epoch 5/50
1069/1069 [==============================] - 0s 89us/step - loss: 0.6789 - acc: 0.5463
Epoch 6/50
1069/1069 [==============================] - 0s 87us/step - loss: 0.6638 - acc: 0.5650
Epoch 7/50
1069/1069 [==============================] - 0s 87us/step - loss: 0.6442 - acc: 0.6183
Epoch 8/50
1069/1069 

...

1070/1070 [==============================] - 0s 27us/step - loss: 0.5665 - acc: 0.7131
Epoch 29/100
1070/1070 [==============================] - 0s 29us/step - loss: 0.5633 - acc: 0.7150
Epoch 30/100
1070/1070 [==============================] - 0s 28us/step - loss: 0.5612 - acc: 0.7159
Epoch 31/100
1070/1070 [==============================] - 0s 29us/step - loss: 0.5627 - acc: 0.7196
Epoch 32/100
1070/1070 [==============================] - 0s 28us/step - loss: 0.5625 - acc: 0.7103
Epoch 33/100
1070/1070 [==============================] - 0s 29us/step - loss: 0.5600 - acc: 0.7140
Epoch 34/100
1070/1070 [==============================] - 0s 28us/step - loss: 0.5581 - acc: 0.7093
Epoch 35/100
1070/1070 [==============================] - 0s 29us/step - loss: 0.5527 - acc: 0.7168
Epoch 36/100
1070/1070 [==============================] - 0s 29us/step - loss: 0.5514 - acc: 0.7178
Epoch 37/100
1070/1070 [==============================] - 0s 27us/step - loss: 0.5517 - acc: 0.7178
Epoch 38/100


1069/1069 [==============================] - 0s 22us/step - loss: 0.6802 - acc: 0.5538
Epoch 10/10
1069/1069 [==============================] - 0s 14us/step
Epoch 1/10
1069/1069 [==============================] - 4s 4ms/step - loss: 0.6923 - acc: 0.5463
Epoch 2/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6908 - acc: 0.5463
Epoch 3/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6897 - acc: 0.5463
Epoch 4/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6891 - acc: 0.5463
Epoch 5/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6883 - acc: 0.5463
Epoch 6/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6876 - acc: 0.5463
Epoch 7/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6864 - acc: 0.5463
Epoch 8/10
1069/1069 [==============================] - 0s 22us/step - loss: 0.6849 - acc: 0.5463
Epoch 9/10
1069/1069 [==============================] - 0s 2

1070/1070 [==============================] - 0s 24us/step - loss: 0.5493 - acc: 0.7168
Epoch 39/50
1070/1070 [==============================] - 0s 24us/step - loss: 0.5493 - acc: 0.7215
Epoch 40/50
1070/1070 [==============================] - 0s 25us/step - loss: 0.5474 - acc: 0.7215
Epoch 41/50
1070/1070 [==============================] - 0s 25us/step - loss: 0.5462 - acc: 0.7252
Epoch 42/50
1070/1070 [==============================] - 0s 23us/step - loss: 0.5468 - acc: 0.7243
Epoch 43/50
1070/1070 [==============================] - 0s 24us/step - loss: 0.5436 - acc: 0.7271
Epoch 44/50
1070/1070 [==============================] - 0s 25us/step - loss: 0.5417 - acc: 0.7280
Epoch 45/50
1070/1070 [==============================] - 0s 25us/step - loss: 0.5405 - acc: 0.7280
Epoch 46/50
1070/1070 [==============================] - 0s 26us/step - loss: 0.5412 - acc: 0.7243
Epoch 47/50
1070/1070 [==============================] - 0s 24us/step - loss: 0.5386 - acc: 0.7271
Epoch 48/50
1070/1070 

Epoch 49/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5375 - acc: 0.6997
Epoch 50/100
1069/1069 [==============================] - 0s 23us/step - loss: 0.5373 - acc: 0.7007
Epoch 51/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5353 - acc: 0.7044
Epoch 52/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5345 - acc: 0.6950
Epoch 53/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5352 - acc: 0.7016
Epoch 54/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5330 - acc: 0.6969
Epoch 55/100
1069/1069 [==============================] - 0s 23us/step - loss: 0.5325 - acc: 0.7016
Epoch 56/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5320 - acc: 0.7025
Epoch 57/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5311 - acc: 0.7044
Epoch 58/100
1069/1069 [==============================] - 0s 22us/step - loss: 0.5289 - acc: 0.7063


1604/1604 [==============================] - 0s 238us/step - loss: 0.5574 - acc: 0.6852
Epoch 10/100
1604/1604 [==============================] - 0s 222us/step - loss: 0.5515 - acc: 0.6989
Epoch 11/100
1604/1604 [==============================] - 0s 222us/step - loss: 0.5501 - acc: 0.7014
Epoch 12/100
1604/1604 [==============================] - 0s 228us/step - loss: 0.5474 - acc: 0.6951
Epoch 13/100
1604/1604 [==============================] - 0s 229us/step - loss: 0.5451 - acc: 0.6989
Epoch 14/100
1604/1604 [==============================] - 0s 224us/step - loss: 0.5382 - acc: 0.7026
Epoch 15/100
1604/1604 [==============================] - 0s 227us/step - loss: 0.5380 - acc: 0.7070
Epoch 16/100
1604/1604 [==============================] - 0s 224us/step - loss: 0.5358 - acc: 0.7076
Epoch 17/100
1604/1604 [==============================] - 0s 204us/step - loss: 0.5339 - acc: 0.7076
Epoch 18/100
1604/1604 [==============================] - 0s 205us/step - loss: 0.5328 - acc: 0.7101
Epo

The winning combination is: <b>{'epochs': 100, 'batch_size': 10}<b> 

### Tune optimizer

In [20]:
# Function to create model, required for KerasClassifier
def create_model(optimizer='adam'):
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer='normal', activation='relu'))
    model.add(Dense(30, kernel_initializer='normal', activation='relu'))
    model.add(Dense(1, kernel_initializer='normal', activation='sigmoid'))
    
    # Compile model
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model
# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
optimizer = ['SGD', 'RMSprop', 'Adagrad', 'Adadelta', 'Adam', 'Adamax', 'Nadam']
param_grid = dict(optimizer=optimizer)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 4s 4ms/step - loss: 0.6919 - acc: 0.5482
Epoch 2/100
1069/1069 [==============================] - 0s 201us/step - loss: 0.6897 - acc: 0.5575
Epoch 3/100
1069/1069 [==============================] - 0s 207us/step - loss: 0.6884 - acc: 0.5575
Epoch 4/100
1069/1069 [==============================] - 0s 207us/step - loss: 0.6877 - acc: 0.5575
Epoch 5/100
1069/1069 [==============================] - 0s 191us/step - loss: 0.6873 - acc: 0.5575
Epoch 6/100
1069/1069 [==============================] - 0s 187us/step - loss: 0.6870 - acc: 0.5575
Epoch 7/100
1069/1069 [==============================] - 0s 195us/step - loss: 0.6868 - acc: 0.5575
Epoch 8/100
1069/1069 [==============================] - 0s 195us/step - loss: 0.6867 - acc: 0.5575
Epoch 9/100
1069/1069 [==============================] - 0s 192us/step - loss: 0.6867 - acc: 0.5575
Epoch 10/100
1069/1069 [==============================] - 0s 190us/step - loss: 0.6866 - acc: 0.5575
E

1069/1069 [==============================] - 0s 187us/step - loss: 0.6881 - acc: 0.5463
Epoch 63/100
1069/1069 [==============================] - 0s 186us/step - loss: 0.6881 - acc: 0.5463
Epoch 64/100
1069/1069 [==============================] - 0s 187us/step - loss: 0.6880 - acc: 0.5463
Epoch 65/100
1069/1069 [==============================] - 0s 188us/step - loss: 0.6880 - acc: 0.5463
Epoch 66/100
1069/1069 [==============================] - 0s 188us/step - loss: 0.6879 - acc: 0.5463
Epoch 67/100
1069/1069 [==============================] - 0s 187us/step - loss: 0.6879 - acc: 0.5463
Epoch 68/100
1069/1069 [==============================] - 0s 187us/step - loss: 0.6879 - acc: 0.5463
Epoch 69/100
1069/1069 [==============================] - 0s 189us/step - loss: 0.6879 - acc: 0.5463
Epoch 70/100
1069/1069 [==============================] - 0s 187us/step - loss: 0.6878 - acc: 0.5463
Epoch 71/100
1069/1069 [==============================] - 0s 186us/step - loss: 0.6877 - acc: 0.5463
Epo

1069/1069 [==============================] - 0s 197us/step - loss: 0.5393 - acc: 0.6941
Epoch 22/100
1069/1069 [==============================] - 0s 201us/step - loss: 0.5394 - acc: 0.6932
Epoch 23/100
1069/1069 [==============================] - 0s 197us/step - loss: 0.5363 - acc: 0.6978
Epoch 24/100
1069/1069 [==============================] - 0s 201us/step - loss: 0.5358 - acc: 0.6969
Epoch 25/100
1069/1069 [==============================] - 0s 199us/step - loss: 0.5336 - acc: 0.6960
Epoch 26/100
1069/1069 [==============================] - 0s 202us/step - loss: 0.5341 - acc: 0.7007
Epoch 27/100
1069/1069 [==============================] - 0s 199us/step - loss: 0.5330 - acc: 0.6960
Epoch 28/100
1069/1069 [==============================] - 0s 199us/step - loss: 0.5360 - acc: 0.6978
Epoch 29/100
1069/1069 [==============================] - 0s 199us/step - loss: 0.5320 - acc: 0.6894
Epoch 30/100
1069/1069 [==============================] - 0s 198us/step - loss: 0.5275 - acc: 0.7016
Epo

1069/1069 [==============================] - 5s 4ms/step - loss: 0.6918 - acc: 0.5482
Epoch 2/100
1069/1069 [==============================] - 0s 215us/step - loss: 0.6900 - acc: 0.5463
Epoch 3/100
1069/1069 [==============================] - 0s 222us/step - loss: 0.6886 - acc: 0.5463
Epoch 4/100
1069/1069 [==============================] - 0s 206us/step - loss: 0.6866 - acc: 0.5463
Epoch 5/100
1069/1069 [==============================] - 0s 205us/step - loss: 0.6825 - acc: 0.5463
Epoch 6/100
1069/1069 [==============================] - 0s 203us/step - loss: 0.6766 - acc: 0.5463
Epoch 7/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6656 - acc: 0.5500
Epoch 8/100
1069/1069 [==============================] - 0s 207us/step - loss: 0.6528 - acc: 0.5809
Epoch 9/100
1069/1069 [==============================] - 0s 199us/step - loss: 0.6362 - acc: 0.6118
Epoch 10/100
1069/1069 [==============================] - 0s 194us/step - loss: 0.6213 - acc: 0.6193
Epoch 11/100


1070/1070 [==============================] - 0s 195us/step - loss: 0.5053 - acc: 0.7449
Epoch 63/100
1070/1070 [==============================] - 0s 195us/step - loss: 0.5002 - acc: 0.7514
Epoch 64/100
1070/1070 [==============================] - 0s 195us/step - loss: 0.5041 - acc: 0.7393
Epoch 65/100
1070/1070 [==============================] - 0s 196us/step - loss: 0.5068 - acc: 0.7430
Epoch 66/100
1070/1070 [==============================] - 0s 193us/step - loss: 0.5008 - acc: 0.7458
Epoch 67/100
1070/1070 [==============================] - 0s 195us/step - loss: 0.5007 - acc: 0.7411
Epoch 68/100
1070/1070 [==============================] - 0s 197us/step - loss: 0.4980 - acc: 0.7486
Epoch 69/100
1070/1070 [==============================] - 0s 197us/step - loss: 0.4994 - acc: 0.7467
Epoch 70/100
1070/1070 [==============================] - 0s 197us/step - loss: 0.4987 - acc: 0.7449
Epoch 71/100
1070/1070 [==============================] - 0s 197us/step - loss: 0.4977 - acc: 0.7458
Epo

...

1069/1069 [==============================] - 0s 212us/step - loss: 0.5592 - acc: 0.6829
Epoch 23/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.5584 - acc: 0.6782
Epoch 24/100
1069/1069 [==============================] - 0s 213us/step - loss: 0.5555 - acc: 0.6848
Epoch 25/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.5533 - acc: 0.6876
Epoch 26/100
1069/1069 [==============================] - 0s 213us/step - loss: 0.5530 - acc: 0.6969
Epoch 27/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.5495 - acc: 0.6857
Epoch 28/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.5499 - acc: 0.6848
Epoch 29/100
1069/1069 [==============================] - 0s 212us/step - loss: 0.5484 - acc: 0.6866
Epoch 30/100
1069/1069 [==============================] - 0s 210us/step - loss: 0.5458 - acc: 0.6904
Epoch 31/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.5474 - acc: 0.6941
Epo

1069/1069 [==============================] - 0s 217us/step - loss: 0.5058 - acc: 0.7334
Epoch 84/100
1069/1069 [==============================] - 0s 216us/step - loss: 0.5055 - acc: 0.7268
Epoch 85/100
1069/1069 [==============================] - 0s 216us/step - loss: 0.5056 - acc: 0.7268
Epoch 86/100
1069/1069 [==============================] - 0s 216us/step - loss: 0.5071 - acc: 0.7278
Epoch 87/100
1069/1069 [==============================] - 0s 217us/step - loss: 0.5048 - acc: 0.7166
Epoch 88/100
1069/1069 [==============================] - 0s 217us/step - loss: 0.5050 - acc: 0.7250
Epoch 89/100
1069/1069 [==============================] - 0s 213us/step - loss: 0.5022 - acc: 0.7212
Epoch 90/100
1069/1069 [==============================] - 0s 214us/step - loss: 0.5052 - acc: 0.7138
Epoch 91/100
1069/1069 [==============================] - 0s 214us/step - loss: 0.5057 - acc: 0.7268
Epoch 92/100
1069/1069 [==============================] - 0s 214us/step - loss: 0.5042 - acc: 0.7259
Epo

1069/1069 [==============================] - 0s 222us/step - loss: 0.5253 - acc: 0.7007
Epoch 44/100
1069/1069 [==============================] - 0s 227us/step - loss: 0.5243 - acc: 0.7007
Epoch 45/100
1069/1069 [==============================] - 0s 227us/step - loss: 0.5269 - acc: 0.6988
Epoch 46/100
1069/1069 [==============================] - 0s 223us/step - loss: 0.5256 - acc: 0.7025
Epoch 47/100
1069/1069 [==============================] - 0s 228us/step - loss: 0.5272 - acc: 0.6988
Epoch 48/100
1069/1069 [==============================] - 0s 225us/step - loss: 0.5230 - acc: 0.7025
Epoch 49/100
1069/1069 [==============================] - 0s 225us/step - loss: 0.5236 - acc: 0.7007
Epoch 50/100
1069/1069 [==============================] - 0s 222us/step - loss: 0.5241 - acc: 0.6978
Epoch 51/100
1069/1069 [==============================] - 0s 223us/step - loss: 0.5249 - acc: 0.7081
Epoch 52/100
1069/1069 [==============================] - 0s 223us/step - loss: 0.5244 - acc: 0.6988
Epo

1070/1070 [==============================] - 0s 248us/step - loss: 0.6050 - acc: 0.6832
Epoch 4/100
1070/1070 [==============================] - 0s 252us/step - loss: 0.5750 - acc: 0.7112
Epoch 5/100
1070/1070 [==============================] - 0s 247us/step - loss: 0.5667 - acc: 0.7084
Epoch 6/100
1070/1070 [==============================] - 0s 251us/step - loss: 0.5566 - acc: 0.7159
Epoch 7/100
1070/1070 [==============================] - 0s 245us/step - loss: 0.5569 - acc: 0.7093
Epoch 8/100
1070/1070 [==============================] - 0s 237us/step - loss: 0.5534 - acc: 0.7140
Epoch 9/100
1070/1070 [==============================] - 0s 247us/step - loss: 0.5496 - acc: 0.7150
Epoch 10/100
1070/1070 [==============================] - 0s 248us/step - loss: 0.5468 - acc: 0.7159
Epoch 11/100
1070/1070 [==============================] - 0s 247us/step - loss: 0.5461 - acc: 0.7121
Epoch 12/100
1070/1070 [==============================] - 0s 251us/step - loss: 0.5448 - acc: 0.7168
Epoch 13/

1604/1604 [==============================] - 0s 222us/step - loss: 0.4978 - acc: 0.7413
Epoch 64/100
1604/1604 [==============================] - 0s 219us/step - loss: 0.5036 - acc: 0.7319
Epoch 65/100
1604/1604 [==============================] - 0s 216us/step - loss: 0.4997 - acc: 0.7357
Epoch 66/100
1604/1604 [==============================] - 0s 218us/step - loss: 0.5021 - acc: 0.7382
Epoch 67/100
1604/1604 [==============================] - 0s 218us/step - loss: 0.5017 - acc: 0.7344
Epoch 68/100
1604/1604 [==============================] - 0s 215us/step - loss: 0.5034 - acc: 0.7325
Epoch 69/100
1604/1604 [==============================] - 0s 206us/step - loss: 0.5031 - acc: 0.7369
Epoch 70/100
1604/1604 [==============================] - 0s 208us/step - loss: 0.5021 - acc: 0.7313
Epoch 71/100
1604/1604 [==============================] - 0s 219us/step - loss: 0.4975 - acc: 0.7363
Epoch 72/100
1604/1604 [==============================] - 0s 217us/step - loss: 0.4989 - acc: 0.7444
Epo

The winner: <b>RMSprop<b>

### Tune Learning Rate and Momentum on SDG

Let's see what kind of improvement can we get with an SDG (Stochastic Gradient Descent) optimizer by playing with the learning rate and the momentum.

In [22]:
# Function to create model, required for KerasClassifier
def create_model(learn_rate=0.01, momentum=0):
   
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer='normal', activation='relu'))
    model.add(Dense(30, kernel_initializer='normal', activation='relu'))
    model.add(Dense(1, kernel_initializer='normal', activation='sigmoid'))
    
    # Compile model
    optimizer = SGD(lr=learn_rate, momentum=momentum)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
learn_rate = [0.001, 0.01, 0.1, 0.2, 0.3]
momentum = [0.0, 0.2, 0.4, 0.6, 0.8, 0.9]
param_grid = dict(learn_rate=learn_rate, momentum=momentum)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 5s 5ms/step - loss: 0.6932 - acc: 0.4949
Epoch 2/100
1069/1069 [==============================] - 0s 237us/step - loss: 0.6928 - acc: 0.5575
Epoch 3/100
1069/1069 [==============================] - 0s 229us/step - loss: 0.6925 - acc: 0.5575
Epoch 4/100
1069/1069 [==============================] - 0s 237us/step - loss: 0.6922 - acc: 0.5575
Epoch 5/100
1069/1069 [==============================] - 0s 234us/step - loss: 0.6919 - acc: 0.5575
Epoch 6/100
1069/1069 [==============================] - 0s 239us/step - loss: 0.6916 - acc: 0.5575
Epoch 7/100
1069/1069 [==============================] - 0s 237us/step - loss: 0.6913 - acc: 0.5575
Epoch 8/100
1069/1069 [==============================] - 0s 244us/step - loss: 0.6910 - acc: 0.5575
Epoch 9/100
1069/1069 [==============================] - 0s 238us/step - loss: 0.6908 - acc: 0.5575
Epoch 10/100
1069/1069 [==============================] - 0s 234us/step - loss: 0.6906 - acc: 0.5575
E

1069/1069 [==============================] - 0s 212us/step - loss: 0.6890 - acc: 0.5463
Epoch 63/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 64/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 65/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 66/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 67/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 68/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 69/100
1069/1069 [==============================] - 0s 209us/step - loss: 0.6890 - acc: 0.5463
Epoch 70/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6890 - acc: 0.5463
Epoch 71/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6889 - acc: 0.5463
Epo

1069/1069 [==============================] - 0s 232us/step - loss: 0.6881 - acc: 0.5575
Epoch 22/100
1069/1069 [==============================] - 0s 232us/step - loss: 0.6880 - acc: 0.5575
Epoch 23/100
1069/1069 [==============================] - 0s 230us/step - loss: 0.6879 - acc: 0.5575
Epoch 24/100
1069/1069 [==============================] - 0s 234us/step - loss: 0.6878 - acc: 0.5575
Epoch 25/100
1069/1069 [==============================] - 0s 230us/step - loss: 0.6877 - acc: 0.5575
Epoch 26/100
1069/1069 [==============================] - 0s 229us/step - loss: 0.6876 - acc: 0.5575
Epoch 27/100
1069/1069 [==============================] - 0s 229us/step - loss: 0.6875 - acc: 0.5575
Epoch 28/100
1069/1069 [==============================] - 0s 227us/step - loss: 0.6875 - acc: 0.5575
Epoch 29/100
1069/1069 [==============================] - 0s 230us/step - loss: 0.6874 - acc: 0.5575
Epoch 30/100
1069/1069 [==============================] - 0s 229us/step - loss: 0.6873 - acc: 0.5575
Epo

1069/1069 [==============================] - 5s 5ms/step - loss: 0.6929 - acc: 0.5482
Epoch 2/100
1069/1069 [==============================] - 0s 240us/step - loss: 0.6926 - acc: 0.5463
Epoch 3/100
1069/1069 [==============================] - 0s 239us/step - loss: 0.6924 - acc: 0.5463
Epoch 4/100
1069/1069 [==============================] - 0s 235us/step - loss: 0.6921 - acc: 0.5463
Epoch 5/100
1069/1069 [==============================] - 0s 233us/step - loss: 0.6919 - acc: 0.5463
Epoch 6/100
1069/1069 [==============================] - 0s 233us/step - loss: 0.6917 - acc: 0.5463
Epoch 7/100
1069/1069 [==============================] - 0s 223us/step - loss: 0.6915 - acc: 0.5463
Epoch 8/100
1069/1069 [==============================] - 0s 212us/step - loss: 0.6913 - acc: 0.5463
Epoch 9/100
1069/1069 [==============================] - 0s 211us/step - loss: 0.6911 - acc: 0.5463
Epoch 10/100
1069/1069 [==============================] - 0s 209us/step - loss: 0.6910 - acc: 0.5463
Epoch 11/100


1070/1070 [==============================] - 0s 211us/step - loss: 0.6926 - acc: 0.5121
Epoch 63/100
1070/1070 [==============================] - 0s 210us/step - loss: 0.6926 - acc: 0.5121
Epoch 64/100
1070/1070 [==============================] - 0s 212us/step - loss: 0.6926 - acc: 0.5121
Epoch 65/100
1070/1070 [==============================] - 0s 211us/step - loss: 0.6926 - acc: 0.5121
Epoch 66/100
1070/1070 [==============================] - 0s 212us/step - loss: 0.6926 - acc: 0.5121
Epoch 67/100
1070/1070 [==============================] - 0s 211us/step - loss: 0.6926 - acc: 0.5121
Epoch 68/100
1070/1070 [==============================] - 0s 210us/step - loss: 0.6926 - acc: 0.5121
Epoch 69/100
1070/1070 [==============================] - 0s 212us/step - loss: 0.6926 - acc: 0.5121
Epoch 70/100
1070/1070 [==============================] - 0s 212us/step - loss: 0.6926 - acc: 0.5121
Epoch 71/100
1070/1070 [==============================] - 0s 211us/step - loss: 0.6926 - acc: 0.5121
Epo

...

1070/1070 [==============================] - 0s 288us/step - loss: 0.6977 - acc: 0.4785
Epoch 29/100
1070/1070 [==============================] - 0s 286us/step - loss: 0.6980 - acc: 0.5103
Epoch 30/100
1070/1070 [==============================] - 0s 278us/step - loss: 0.6979 - acc: 0.4991
Epoch 31/100
1070/1070 [==============================] - 0s 288us/step - loss: 0.6978 - acc: 0.5009
Epoch 32/100
1070/1070 [==============================] - 0s 289us/step - loss: 0.6977 - acc: 0.5047
Epoch 33/100
1070/1070 [==============================] - 0s 288us/step - loss: 0.6989 - acc: 0.4879
Epoch 34/100
1070/1070 [==============================] - 0s 288us/step - loss: 0.6997 - acc: 0.4710
Epoch 35/100
1070/1070 [==============================] - 0s 290us/step - loss: 0.7003 - acc: 0.4879
Epoch 36/100
1070/1070 [==============================] - 0s 293us/step - loss: 0.6988 - acc: 0.4748
Epoch 37/100
1070/1070 [==============================] - 0s 289us/step - loss: 0.7013 - acc: 0.4710
Epo

1069/1069 [==============================] - 0s 286us/step - loss: 0.6911 - acc: 0.5463
Epoch 90/100
1069/1069 [==============================] - 0s 285us/step - loss: 0.6975 - acc: 0.5182
Epoch 91/100
1069/1069 [==============================] - 0s 280us/step - loss: 0.6979 - acc: 0.5164
Epoch 92/100
1069/1069 [==============================] - 0s 290us/step - loss: 0.6975 - acc: 0.5519
Epoch 93/100
1069/1069 [==============================] - 0s 290us/step - loss: 0.6931 - acc: 0.5426
Epoch 94/100
1069/1069 [==============================] - 0s 295us/step - loss: 0.6959 - acc: 0.5370
Epoch 95/100
1069/1069 [==============================] - 0s 287us/step - loss: 0.6972 - acc: 0.5435
Epoch 96/100
1069/1069 [==============================] - 0s 290us/step - loss: 0.6930 - acc: 0.5500
Epoch 97/100
1069/1069 [==============================] - 0s 285us/step - loss: 0.6932 - acc: 0.5519
Epoch 98/100
1069/1069 [==============================] - 0s 287us/step - loss: 0.6932 - acc: 0.5388
Epo

1070/1070 [==============================] - 0s 268us/step - loss: 0.6992 - acc: 0.5065
Epoch 50/100
1070/1070 [==============================] - 0s 269us/step - loss: 0.6959 - acc: 0.5065
Epoch 51/100
1070/1070 [==============================] - 0s 270us/step - loss: 0.7135 - acc: 0.5009
Epoch 52/100
1070/1070 [==============================] - 0s 267us/step - loss: 0.7006 - acc: 0.5140
Epoch 53/100
1070/1070 [==============================] - 0s 265us/step - loss: 0.7065 - acc: 0.4916
Epoch 54/100
1070/1070 [==============================] - 0s 266us/step - loss: 0.7024 - acc: 0.5028
Epoch 55/100
1070/1070 [==============================] - 0s 268us/step - loss: 0.7011 - acc: 0.5103
Epoch 56/100
1070/1070 [==============================] - 0s 270us/step - loss: 0.6993 - acc: 0.4991
Epoch 57/100
1070/1070 [==============================] - 0s 271us/step - loss: 0.7028 - acc: 0.4972
Epoch 58/100
1070/1070 [==============================] - 0s 318us/step - loss: 0.7020 - acc: 0.4972
Epo

1069/1069 [==============================] - 0s 300us/step - loss: 0.7192 - acc: 0.4939
Epoch 10/100
1069/1069 [==============================] - 0s 297us/step - loss: 0.7232 - acc: 0.4902
Epoch 11/100
1069/1069 [==============================] - 0s 288us/step - loss: 0.7140 - acc: 0.4977
Epoch 12/100
1069/1069 [==============================] - 0s 284us/step - loss: 0.7041 - acc: 0.5164
Epoch 13/100
1069/1069 [==============================] - 0s 279us/step - loss: 0.7116 - acc: 0.5014
Epoch 14/100
1069/1069 [==============================] - 0s 281us/step - loss: 0.7093 - acc: 0.5117
Epoch 15/100
1069/1069 [==============================] - 0s 278us/step - loss: 0.7001 - acc: 0.5182
Epoch 16/100
1069/1069 [==============================] - 0s 279us/step - loss: 0.7373 - acc: 0.4920
Epoch 17/100
1069/1069 [==============================] - 0s 280us/step - loss: 0.7017 - acc: 0.5014
Epoch 18/100
1069/1069 [==============================] - 0s 279us/step - loss: 0.7031 - acc: 0.5248
Epo

1070/1070 [==============================] - 0s 291us/step - loss: 0.7134 - acc: 0.4972
Epoch 71/100
1070/1070 [==============================] - 0s 294us/step - loss: 0.7042 - acc: 0.5009
Epoch 72/100
1070/1070 [==============================] - 0s 289us/step - loss: 0.7058 - acc: 0.5178
Epoch 73/100
1070/1070 [==============================] - 0s 295us/step - loss: 0.7192 - acc: 0.4991
Epoch 74/100
1070/1070 [==============================] - 0s 297us/step - loss: 0.7093 - acc: 0.5215
Epoch 75/100
1070/1070 [==============================] - 0s 294us/step - loss: 0.7200 - acc: 0.4935
Epoch 76/100
1070/1070 [==============================] - 0s 293us/step - loss: 0.7175 - acc: 0.5121
Epoch 77/100
1070/1070 [==============================] - 0s 291us/step - loss: 0.7131 - acc: 0.5103
Epoch 78/100
1070/1070 [==============================] - 0s 294us/step - loss: 0.7055 - acc: 0.5065
Epoch 79/100
1070/1070 [==============================] - 0s 292us/step - loss: 0.7066 - acc: 0.4935
Epo

### Tune Network Weight Initialization

In [26]:
# Function to create model, required for KerasClassifier
def create_model(init_mode='uniform'):
    # create model
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer=init_mode, activation='relu'))
    model.add(Dense(30, kernel_initializer=init_mode, activation='relu'))
    model.add(Dense(1, kernel_initializer=init_mode, activation='sigmoid'))
    
    # Compile model
    optimizer = SGD(lr=0.2, momentum=0.0)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
init_mode = ['uniform', 'lecun_uniform', 'normal', 'zero', 'glorot_normal', 'glorot_uniform', 'he_normal', 'he_uniform']
param_grid = dict(init_mode=init_mode)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 8s 8ms/step - loss: 0.6900 - acc: 0.5575
Epoch 2/100
1069/1069 [==============================] - 0s 364us/step - loss: 0.6876 - acc: 0.5575
Epoch 3/100
1069/1069 [==============================] - 0s 357us/step - loss: 0.6877 - acc: 0.5575
Epoch 4/100
1069/1069 [==============================] - 0s 360us/step - loss: 0.6882 - acc: 0.5575
Epoch 5/100
1069/1069 [==============================] - 0s 306us/step - loss: 0.6878 - acc: 0.5547
Epoch 6/100
1069/1069 [==============================] - 0s 318us/step - loss: 0.6870 - acc: 0.5575
Epoch 7/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.6878 - acc: 0.5575
Epoch 8/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.6870 - acc: 0.5519
Epoch 9/100
1069/1069 [==============================] - 0s 317us/step - loss: 0.6863 - acc: 0.5575
Epoch 10/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.6868 - acc: 0.5575
E

Epoch 62/100
1069/1069 [==============================] - 0s 326us/step - loss: 0.5666 - acc: 0.6707
Epoch 63/100
1069/1069 [==============================] - 0s 324us/step - loss: 0.5607 - acc: 0.6735
Epoch 64/100
1069/1069 [==============================] - 0s 329us/step - loss: 0.5642 - acc: 0.6670
Epoch 65/100
1069/1069 [==============================] - 0s 332us/step - loss: 0.5708 - acc: 0.6632
Epoch 66/100
1069/1069 [==============================] - 0s 317us/step - loss: 0.5585 - acc: 0.6698
Epoch 67/100
1069/1069 [==============================] - 0s 328us/step - loss: 0.5641 - acc: 0.6539
Epoch 68/100
1069/1069 [==============================] - 0s 327us/step - loss: 0.5617 - acc: 0.6754
Epoch 69/100
1069/1069 [==============================] - 0s 328us/step - loss: 0.5681 - acc: 0.6679
Epoch 70/100
1069/1069 [==============================] - 0s 330us/step - loss: 0.5583 - acc: 0.6642
Epoch 71/100
1069/1069 [==============================] - 0s 325us/step - loss: 0.5568 - ac

1069/1069 [==============================] - 0s 320us/step - loss: 0.5384 - acc: 0.7063
Epoch 22/100
1069/1069 [==============================] - 0s 322us/step - loss: 0.5413 - acc: 0.6941
Epoch 23/100
1069/1069 [==============================] - 0s 322us/step - loss: 0.5332 - acc: 0.7007
Epoch 24/100
1069/1069 [==============================] - 0s 319us/step - loss: 0.5439 - acc: 0.6969
Epoch 25/100
1069/1069 [==============================] - 0s 322us/step - loss: 0.5320 - acc: 0.7081
Epoch 26/100
1069/1069 [==============================] - 0s 321us/step - loss: 0.5434 - acc: 0.7016
Epoch 27/100
1069/1069 [==============================] - 0s 322us/step - loss: 0.5322 - acc: 0.7007
Epoch 28/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5361 - acc: 0.6941
Epoch 29/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5374 - acc: 0.7109
Epoch 30/100
1069/1069 [==============================] - 0s 321us/step - loss: 0.5308 - acc: 0.7184
Epo

1069/1069 [==============================] - 8s 8ms/step - loss: 0.6906 - acc: 0.5407
Epoch 2/100
1069/1069 [==============================] - 0s 371us/step - loss: 0.6601 - acc: 0.6015
Epoch 3/100
1069/1069 [==============================] - 0s 371us/step - loss: 0.6478 - acc: 0.6109
Epoch 4/100
1069/1069 [==============================] - 0s 354us/step - loss: 0.6219 - acc: 0.6445
Epoch 5/100
1069/1069 [==============================] - 0s 275us/step - loss: 0.6138 - acc: 0.6483
Epoch 6/100
1069/1069 [==============================] - 0s 361us/step - loss: 0.6021 - acc: 0.6576
Epoch 7/100
1069/1069 [==============================] - 0s 364us/step - loss: 0.5959 - acc: 0.6754
Epoch 8/100
1069/1069 [==============================] - 0s 360us/step - loss: 0.5889 - acc: 0.6445
Epoch 9/100
1069/1069 [==============================] - 0s 359us/step - loss: 0.5946 - acc: 0.6501
Epoch 10/100
1069/1069 [==============================] - 0s 353us/step - loss: 0.5947 - acc: 0.6520
Epoch 11/100


1070/1070 [==============================] - 0s 309us/step - loss: 0.5159 - acc: 0.7421
Epoch 63/100
1070/1070 [==============================] - 0s 274us/step - loss: 0.5028 - acc: 0.7383
Epoch 64/100
1070/1070 [==============================] - 0s 271us/step - loss: 0.5092 - acc: 0.7383
Epoch 65/100
1070/1070 [==============================] - 0s 273us/step - loss: 0.5119 - acc: 0.7393
Epoch 66/100
1070/1070 [==============================] - 0s 283us/step - loss: 0.5063 - acc: 0.7430
Epoch 67/100
1070/1070 [==============================] - 0s 288us/step - loss: 0.5095 - acc: 0.7383
Epoch 68/100
1070/1070 [==============================] - 0s 287us/step - loss: 0.4978 - acc: 0.7551
Epoch 69/100
1070/1070 [==============================] - 0s 289us/step - loss: 0.5035 - acc: 0.7495
Epoch 70/100
1070/1070 [==============================] - 0s 282us/step - loss: 0.5079 - acc: 0.7374
Epoch 71/100
1070/1070 [==============================] - 0s 285us/step - loss: 0.5027 - acc: 0.7439
Epo

...

Epoch 42/100
1069/1069 [==============================] - 0s 345us/step - loss: 0.5222 - acc: 0.7175
Epoch 43/100
1069/1069 [==============================] - 0s 342us/step - loss: 0.5200 - acc: 0.7166
Epoch 44/100
1069/1069 [==============================] - 0s 344us/step - loss: 0.5267 - acc: 0.6988
Epoch 45/100
1069/1069 [==============================] - 0s 345us/step - loss: 0.5220 - acc: 0.7081
Epoch 46/100
1069/1069 [==============================] - 0s 342us/step - loss: 0.5171 - acc: 0.7100
Epoch 47/100
1069/1069 [==============================] - 0s 345us/step - loss: 0.5189 - acc: 0.7166
Epoch 48/100
1069/1069 [==============================] - 0s 337us/step - loss: 0.5243 - acc: 0.7128
Epoch 49/100
1069/1069 [==============================] - 0s 342us/step - loss: 0.5216 - acc: 0.7222
Epoch 50/100
1069/1069 [==============================] - 0s 343us/step - loss: 0.5132 - acc: 0.7147
Epoch 51/100
1069/1069 [==============================] - 0s 342us/step - loss: 0.5169 - ac

1069/1069 [==============================] - 0s 370us/step - loss: 0.5230 - acc: 0.7072
Epoch 23/100
1069/1069 [==============================] - 0s 368us/step - loss: 0.5413 - acc: 0.7100
Epoch 24/100
1069/1069 [==============================] - 0s 368us/step - loss: 0.5398 - acc: 0.7091
Epoch 25/100
1069/1069 [==============================] - 0s 372us/step - loss: 0.5253 - acc: 0.7072
Epoch 26/100
1069/1069 [==============================] - 0s 373us/step - loss: 0.5407 - acc: 0.7063
Epoch 27/100
1069/1069 [==============================] - 0s 373us/step - loss: 0.5395 - acc: 0.6997
Epoch 28/100
1069/1069 [==============================] - 0s 370us/step - loss: 0.5303 - acc: 0.7325
Epoch 29/100
1069/1069 [==============================] - 0s 368us/step - loss: 0.5225 - acc: 0.7250
Epoch 30/100
1069/1069 [==============================] - 0s 363us/step - loss: 0.5336 - acc: 0.7072
Epoch 31/100
1069/1069 [==============================] - 0s 359us/step - loss: 0.5197 - acc: 0.7334
Epo

1070/1070 [==============================] - 0s 327us/step - loss: 0.5053 - acc: 0.7355
Epoch 84/100
1070/1070 [==============================] - 0s 327us/step - loss: 0.4953 - acc: 0.7495
Epoch 85/100
1070/1070 [==============================] - 0s 326us/step - loss: 0.4987 - acc: 0.7421
Epoch 86/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.4910 - acc: 0.7636
Epoch 87/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.4957 - acc: 0.7617
Epoch 88/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.4996 - acc: 0.7551
Epoch 89/100
1070/1070 [==============================] - 0s 326us/step - loss: 0.5023 - acc: 0.7421
Epoch 90/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.5009 - acc: 0.7561
Epoch 91/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.5007 - acc: 0.7579
Epoch 92/100
1070/1070 [==============================] - 0s 325us/step - loss: 0.5038 - acc: 0.7374
Epo

1069/1069 [==============================] - 0s 343us/step - loss: 0.5182 - acc: 0.7194
Epoch 43/100
1069/1069 [==============================] - 0s 339us/step - loss: 0.5077 - acc: 0.7315
Epoch 44/100
1069/1069 [==============================] - 0s 341us/step - loss: 0.5136 - acc: 0.7240
Epoch 45/100
1069/1069 [==============================] - 0s 340us/step - loss: 0.5141 - acc: 0.7268
Epoch 46/100
1069/1069 [==============================] - 0s 339us/step - loss: 0.5203 - acc: 0.7156
Epoch 47/100
1069/1069 [==============================] - 0s 338us/step - loss: 0.5201 - acc: 0.7222
Epoch 48/100
1069/1069 [==============================] - 0s 342us/step - loss: 0.5181 - acc: 0.7315
Epoch 49/100
1069/1069 [==============================] - 0s 341us/step - loss: 0.5108 - acc: 0.7306
Epoch 50/100
1069/1069 [==============================] - 0s 345us/step - loss: 0.5166 - acc: 0.7287
Epoch 51/100
1069/1069 [==============================] - 0s 340us/step - loss: 0.5075 - acc: 0.7325
Epo

1604/1604 [==============================] - 1s 346us/step - loss: 0.6452 - acc: 0.6197
Epoch 3/100
1604/1604 [==============================] - 1s 344us/step - loss: 0.6092 - acc: 0.6658
Epoch 4/100
1604/1604 [==============================] - 1s 345us/step - loss: 0.6012 - acc: 0.6584
Epoch 5/100
1604/1604 [==============================] - 1s 345us/step - loss: 0.5941 - acc: 0.6596
Epoch 6/100
1604/1604 [==============================] - 1s 343us/step - loss: 0.5858 - acc: 0.6796
Epoch 7/100
1604/1604 [==============================] - 1s 344us/step - loss: 0.5714 - acc: 0.6833
Epoch 8/100
1604/1604 [==============================] - 1s 342us/step - loss: 0.5516 - acc: 0.7014
Epoch 9/100
1604/1604 [==============================] - 1s 333us/step - loss: 0.5538 - acc: 0.7007
Epoch 10/100
1604/1604 [==============================] - 1s 332us/step - loss: 0.5532 - acc: 0.6995
Epoch 11/100
1604/1604 [==============================] - 1s 331us/step - loss: 0.5487 - acc: 0.6976
Epoch 12/1

### Tune the Activation Function

In [27]:
# Function to create model, required for KerasClassifier
def create_model(activation='softmax'):
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dense(30, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dense(1, kernel_initializer='he_uniform', activation=activation))
    
    # Compile model
    optimizer = SGD(lr=0.2, momentum=0.0)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
activation = ['softmax', 'softplus', 'softsign', 'relu', 'tanh', 'sigmoid', 'hard_sigmoid', 'linear']
param_grid = dict(activation=activation)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 9s 8ms/step - loss: 8.8884 - acc: 0.4425
Epoch 2/100
1069/1069 [==============================] - 0s 382us/step - loss: 8.8884 - acc: 0.4425
Epoch 3/100
1069/1069 [==============================] - 0s 376us/step - loss: 8.8884 - acc: 0.4425
Epoch 4/100
1069/1069 [==============================] - 0s 373us/step - loss: 8.8884 - acc: 0.4425
Epoch 5/100
1069/1069 [==============================] - 0s 371us/step - loss: 8.8884 - acc: 0.4425
Epoch 6/100
1069/1069 [==============================] - 0s 362us/step - loss: 8.8884 - acc: 0.4425
Epoch 7/100
1069/1069 [==============================] - 0s 372us/step - loss: 8.8884 - acc: 0.4425
Epoch 8/100
1069/1069 [==============================] - 0s 371us/step - loss: 8.8884 - acc: 0.4425
Epoch 9/100
1069/1069 [==============================] - 0s 371us/step - loss: 8.8884 - acc: 0.4425
Epoch 10/100
1069/1069 [==============================] - 0s 369us/step - loss: 8.8884 - acc: 0.4425
E

1069/1069 [==============================] - 0s 347us/step - loss: 8.7094 - acc: 0.4537
Epoch 63/100
1069/1069 [==============================] - 0s 347us/step - loss: 8.7094 - acc: 0.4537
Epoch 64/100
1069/1069 [==============================] - 0s 349us/step - loss: 8.7094 - acc: 0.4537
Epoch 65/100
1069/1069 [==============================] - 0s 345us/step - loss: 8.7094 - acc: 0.4537
Epoch 66/100
1069/1069 [==============================] - 0s 346us/step - loss: 8.7094 - acc: 0.4537
Epoch 67/100
1069/1069 [==============================] - 0s 344us/step - loss: 8.7094 - acc: 0.4537
Epoch 68/100
1069/1069 [==============================] - 0s 343us/step - loss: 8.7094 - acc: 0.4537
Epoch 69/100
1069/1069 [==============================] - 0s 333us/step - loss: 8.7094 - acc: 0.4537
Epoch 70/100
1069/1069 [==============================] - 0s 333us/step - loss: 8.7094 - acc: 0.4537
Epoch 71/100
1069/1069 [==============================] - 0s 334us/step - loss: 8.7094 - acc: 0.4537
Epo

1069/1069 [==============================] - 0s 347us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 22/100
1069/1069 [==============================] - 0s 352us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 23/100
1069/1069 [==============================] - 0s 349us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 24/100
1069/1069 [==============================] - 0s 354us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 25/100
1069/1069 [==============================] - 0s 349us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 26/100
1069/1069 [==============================] - 0s 352us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 27/100
1069/1069 [==============================] - 0s 356us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 28/100
1069/1069 [==============================] - 0s 348us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 29/100
1069/1069 [==============================] - 0s 338us/step - loss: 8.8884 - acc: 0.0000e+00
Epoch 30/100
1069/1069 [==============================] - 0s 341us/s

1069/1069 [==============================] - 0s 304us/step - loss: 0.5060 - acc: 0.7250
Epoch 80/100
1069/1069 [==============================] - 0s 302us/step - loss: 0.5098 - acc: 0.7259
Epoch 81/100
1069/1069 [==============================] - 0s 304us/step - loss: 0.5120 - acc: 0.7222
Epoch 82/100
1069/1069 [==============================] - 0s 303us/step - loss: 0.5047 - acc: 0.7371
Epoch 83/100
1069/1069 [==============================] - 0s 301us/step - loss: 0.5113 - acc: 0.7343
Epoch 84/100
1069/1069 [==============================] - 0s 303us/step - loss: 0.5196 - acc: 0.7343
Epoch 85/100
1069/1069 [==============================] - 0s 301us/step - loss: 0.5102 - acc: 0.7231
Epoch 86/100
1069/1069 [==============================] - 0s 302us/step - loss: 0.5101 - acc: 0.7325
Epoch 87/100
1069/1069 [==============================] - 0s 304us/step - loss: 0.5072 - acc: 0.7353
Epoch 88/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4997 - acc: 0.7381
Epo

1069/1069 [==============================] - 0s 336us/step - loss: 7.1318 - acc: 0.5360
Epoch 39/100
1069/1069 [==============================] - 0s 337us/step - loss: 7.1318 - acc: 0.5360
Epoch 40/100
1069/1069 [==============================] - 0s 335us/step - loss: 7.1318 - acc: 0.5360
Epoch 41/100
1069/1069 [==============================] - 0s 339us/step - loss: 7.1318 - acc: 0.5360
Epoch 42/100
1069/1069 [==============================] - 0s 336us/step - loss: 7.1318 - acc: 0.5360
Epoch 43/100
1069/1069 [==============================] - 0s 339us/step - loss: 7.1318 - acc: 0.5360
Epoch 44/100
1069/1069 [==============================] - 0s 337us/step - loss: 7.1318 - acc: 0.5360
Epoch 45/100
1069/1069 [==============================] - 0s 337us/step - loss: 7.1318 - acc: 0.5360
Epoch 46/100
1069/1069 [==============================] - 0s 336us/step - loss: 7.1318 - acc: 0.5360
Epoch 47/100
1069/1069 [==============================] - 0s 338us/step - loss: 7.1318 - acc: 0.5360
Epo

...

1069/1069 [==============================] - 0s 358us/step - loss: 8.8884 - acc: 0.4425
Epoch 32/100
1069/1069 [==============================] - 0s 357us/step - loss: 8.8884 - acc: 0.4425
Epoch 33/100
1069/1069 [==============================] - 0s 357us/step - loss: 8.8884 - acc: 0.4425
Epoch 34/100
1069/1069 [==============================] - 0s 359us/step - loss: 8.8884 - acc: 0.4425
Epoch 35/100
1069/1069 [==============================] - 0s 356us/step - loss: 8.8884 - acc: 0.4425
Epoch 36/100
1069/1069 [==============================] - 0s 358us/step - loss: 8.8884 - acc: 0.4425
Epoch 37/100
1069/1069 [==============================] - 0s 358us/step - loss: 8.8884 - acc: 0.4425
Epoch 38/100
1069/1069 [==============================] - 0s 358us/step - loss: 8.8884 - acc: 0.4425
Epoch 39/100
1069/1069 [==============================] - 0s 357us/step - loss: 8.8884 - acc: 0.4425
Epoch 40/100
1069/1069 [==============================] - 0s 356us/step - loss: 8.8884 - acc: 0.4425
Epo

1069/1069 [==============================] - 0s 404us/step - loss: 7.3127 - acc: 0.5463
Epoch 93/100
1069/1069 [==============================] - 0s 371us/step - loss: 7.3127 - acc: 0.5463
Epoch 94/100
1069/1069 [==============================] - 0s 370us/step - loss: 7.3127 - acc: 0.5463
Epoch 95/100
1069/1069 [==============================] - 0s 371us/step - loss: 7.3127 - acc: 0.5463
Epoch 96/100
1069/1069 [==============================] - 0s 369us/step - loss: 7.3127 - acc: 0.5463
Epoch 97/100
1069/1069 [==============================] - 0s 369us/step - loss: 7.3127 - acc: 0.5463
Epoch 98/100
1069/1069 [==============================] - 0s 368us/step - loss: 7.3127 - acc: 0.5463
Epoch 99/100
1069/1069 [==============================] - 0s 368us/step - loss: 7.3127 - acc: 0.5463
Epoch 100/100
1069/1069 [==============================] - 0s 302us/step
Epoch 1/100
1070/1070 [==============================] - 9s 8ms/step - loss: 0.6863 - acc: 0.5570
Epoch 2/100
1070/1070 [===========

1069/1069 [==============================] - 0s 306us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 51/100
1069/1069 [==============================] - 0s 306us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 52/100
1069/1069 [==============================] - 0s 305us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 53/100
1069/1069 [==============================] - 0s 306us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 54/100
1069/1069 [==============================] - 0s 306us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 55/100
1069/1069 [==============================] - 0s 306us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 56/100
1069/1069 [==============================] - 0s 308us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 57/100
1069/1069 [==============================] - 0s 313us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 58/100
1069/1069 [==============================] - 0s 313us/step - loss: 7.1318 - acc: 0.0000e+00
Epoch 59/100
1069/1069 [==============================] - 0s 313us/s

1070/1070 [==============================] - 0s 379us/step - loss: 7.7775 - acc: 0.2402
Epoch 5/100
1070/1070 [==============================] - 0s 372us/step - loss: 7.7775 - acc: 0.2402
Epoch 6/100
1070/1070 [==============================] - 0s 371us/step - loss: 7.7775 - acc: 0.2402
Epoch 7/100
1070/1070 [==============================] - 0s 371us/step - loss: 7.7775 - acc: 0.2402
Epoch 8/100
1070/1070 [==============================] - 0s 372us/step - loss: 7.7775 - acc: 0.2402
Epoch 9/100
1070/1070 [==============================] - 0s 371us/step - loss: 7.7775 - acc: 0.2402
Epoch 10/100
1070/1070 [==============================] - 0s 371us/step - loss: 7.7775 - acc: 0.2402
Epoch 11/100
1070/1070 [==============================] - 0s 370us/step - loss: 7.7775 - acc: 0.2402
Epoch 12/100
1070/1070 [==============================] - 0s 374us/step - loss: 7.7775 - acc: 0.2402
Epoch 13/100
1070/1070 [==============================] - 0s 367us/step - loss: 7.7775 - acc: 0.2402
Epoch 14

1604/1604 [==============================] - 0s 310us/step - loss: 0.5042 - acc: 0.7419
Epoch 66/100
1604/1604 [==============================] - 0s 307us/step - loss: 0.4999 - acc: 0.7406
Epoch 67/100
1604/1604 [==============================] - 0s 311us/step - loss: 0.5071 - acc: 0.7363
Epoch 68/100
1604/1604 [==============================] - 0s 311us/step - loss: 0.4976 - acc: 0.7344
Epoch 69/100
1604/1604 [==============================] - 1s 321us/step - loss: 0.5085 - acc: 0.7357
Epoch 70/100
1604/1604 [==============================] - 1s 316us/step - loss: 0.5038 - acc: 0.7363
Epoch 71/100
1604/1604 [==============================] - 1s 313us/step - loss: 0.5031 - acc: 0.7394
Epoch 72/100
1604/1604 [==============================] - 1s 326us/step - loss: 0.5079 - acc: 0.7394
Epoch 73/100
1604/1604 [==============================] - 1s 330us/step - loss: 0.5043 - acc: 0.7369
Epoch 74/100
1604/1604 [==============================] - 1s 326us/step - loss: 0.5071 - acc: 0.7338
Epo

### Tune Dropout Regularization

In [28]:
# Function to create model, required for KerasClassifier
def create_model(dropout_rate=0.0, weight_constraint=0):
    # create model
    model = Sequential()
    model.add(Dense(60, input_dim=8, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(30, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(1, kernel_initializer='he_uniform', activation='sigmoid'))
    
    # Compile model
    optimizer = SGD(lr=0.2, momentum=0.0)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
weight_constraint = [1, 2, 3, 4, 5]
dropout_rate = [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
param_grid = dict(dropout_rate=dropout_rate, weight_constraint=weight_constraint)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 10s 9ms/step - loss: 0.6950 - acc: 0.5585
Epoch 2/100
1069/1069 [==============================] - 0s 412us/step - loss: 0.6553 - acc: 0.5940
Epoch 3/100
1069/1069 [==============================] - 0s 366us/step - loss: 0.6333 - acc: 0.6352
Epoch 4/100
1069/1069 [==============================] - 0s 363us/step - loss: 0.6093 - acc: 0.6529
Epoch 5/100
1069/1069 [==============================] - 0s 350us/step - loss: 0.6011 - acc: 0.6567
Epoch 6/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5784 - acc: 0.6717
Epoch 7/100
1069/1069 [==============================] - 0s 324us/step - loss: 0.5697 - acc: 0.6670
Epoch 8/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5820 - acc: 0.6745
Epoch 9/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5831 - acc: 0.6539
Epoch 10/100
1069/1069 [==============================] - 0s 320us/step - loss: 0.5573 - acc: 0.6857


1069/1069 [==============================] - 0s 396us/step - loss: 0.5045 - acc: 0.7343
Epoch 63/100
1069/1069 [==============================] - 0s 406us/step - loss: 0.5106 - acc: 0.7306
Epoch 64/100
1069/1069 [==============================] - 0s 396us/step - loss: 0.5148 - acc: 0.7315
Epoch 65/100
1069/1069 [==============================] - 0s 417us/step - loss: 0.5138 - acc: 0.7353
Epoch 66/100
1069/1069 [==============================] - 0s 393us/step - loss: 0.5001 - acc: 0.7409
Epoch 67/100
1069/1069 [==============================] - 0s 391us/step - loss: 0.5054 - acc: 0.7371
Epoch 68/100
1069/1069 [==============================] - 0s 395us/step - loss: 0.5066 - acc: 0.7297
Epoch 69/100
1069/1069 [==============================] - 0s 387us/step - loss: 0.5201 - acc: 0.7231
Epoch 70/100
1069/1069 [==============================] - 0s 391us/step - loss: 0.4990 - acc: 0.7371
Epoch 71/100
1069/1069 [==============================] - 0s 389us/step - loss: 0.5083 - acc: 0.7315
Epo

1069/1069 [==============================] - 0s 362us/step - loss: 0.5384 - acc: 0.7156
Epoch 23/100
1069/1069 [==============================] - 0s 362us/step - loss: 0.5249 - acc: 0.7091
Epoch 24/100
1069/1069 [==============================] - 0s 362us/step - loss: 0.5364 - acc: 0.7044
Epoch 25/100
1069/1069 [==============================] - 0s 363us/step - loss: 0.5252 - acc: 0.7222
Epoch 26/100
1069/1069 [==============================] - 0s 364us/step - loss: 0.5400 - acc: 0.6978
Epoch 27/100
1069/1069 [==============================] - 0s 362us/step - loss: 0.5272 - acc: 0.7016
Epoch 28/100
1069/1069 [==============================] - 0s 363us/step - loss: 0.5264 - acc: 0.7091
Epoch 29/100
1069/1069 [==============================] - 0s 364us/step - loss: 0.5323 - acc: 0.7016
Epoch 30/100
1069/1069 [==============================] - 0s 360us/step - loss: 0.5256 - acc: 0.7203
Epoch 31/100
1069/1069 [==============================] - 0s 361us/step - loss: 0.5256 - acc: 0.7109
Epo

1069/1069 [==============================] - 0s 310us/step - loss: 0.5093 - acc: 0.7278
Epoch 84/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5086 - acc: 0.7306
Epoch 85/100
1069/1069 [==============================] - 0s 308us/step - loss: 0.5083 - acc: 0.7278
Epoch 86/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5033 - acc: 0.7287
Epoch 87/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4990 - acc: 0.7371
Epoch 88/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4934 - acc: 0.7343
Epoch 89/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5159 - acc: 0.7371
Epoch 90/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4956 - acc: 0.7390
Epoch 91/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4989 - acc: 0.7353
Epoch 92/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.4949 - acc: 0.7399
Epo

1069/1069 [==============================] - 0s 410us/step - loss: 0.5195 - acc: 0.7212
Epoch 44/100
1069/1069 [==============================] - 0s 403us/step - loss: 0.5367 - acc: 0.7044
Epoch 45/100
1069/1069 [==============================] - 0s 410us/step - loss: 0.5161 - acc: 0.7175
Epoch 46/100
1069/1069 [==============================] - 0s 409us/step - loss: 0.5167 - acc: 0.7194
Epoch 47/100
1069/1069 [==============================] - 0s 404us/step - loss: 0.5199 - acc: 0.7259
Epoch 48/100
1069/1069 [==============================] - 0s 410us/step - loss: 0.5145 - acc: 0.7175
Epoch 49/100
1069/1069 [==============================] - 0s 407us/step - loss: 0.5167 - acc: 0.7175
Epoch 50/100
1069/1069 [==============================] - 0s 406us/step - loss: 0.5141 - acc: 0.7250
Epoch 51/100
1069/1069 [==============================] - 0s 407us/step - loss: 0.5086 - acc: 0.7231
Epoch 52/100
1069/1069 [==============================] - 0s 405us/step - loss: 0.5203 - acc: 0.7212
Epo

...

1069/1069 [==============================] - 1s 495us/step - loss: 0.9077 - acc: 0.5491
Epoch 69/100
1069/1069 [==============================] - 1s 503us/step - loss: 1.0060 - acc: 0.5463
Epoch 70/100
1069/1069 [==============================] - 0s 443us/step - loss: 0.9642 - acc: 0.5407
Epoch 71/100
1069/1069 [==============================] - 0s 445us/step - loss: 0.9642 - acc: 0.5332
Epoch 72/100
1069/1069 [==============================] - 0s 445us/step - loss: 1.0581 - acc: 0.5426
Epoch 73/100
1069/1069 [==============================] - 0s 443us/step - loss: 0.8369 - acc: 0.5491
Epoch 74/100
1069/1069 [==============================] - 0s 443us/step - loss: 1.0531 - acc: 0.5416
Epoch 75/100
1069/1069 [==============================] - 0s 443us/step - loss: 0.8588 - acc: 0.5398
Epoch 76/100
1069/1069 [==============================] - 0s 455us/step - loss: 0.9081 - acc: 0.5500
Epoch 77/100
1069/1069 [==============================] - 0s 461us/step - loss: 0.9339 - acc: 0.5463
Epo

Epoch 48/100
1070/1070 [==============================] - 0s 462us/step - loss: 0.9913 - acc: 0.4963
Epoch 49/100
1070/1070 [==============================] - 0s 464us/step - loss: 1.0659 - acc: 0.5000
Epoch 50/100
1070/1070 [==============================] - 0s 459us/step - loss: 1.0206 - acc: 0.5121
Epoch 51/100
1070/1070 [==============================] - 0s 464us/step - loss: 1.0756 - acc: 0.5131
Epoch 52/100
1070/1070 [==============================] - 0s 459us/step - loss: 0.9506 - acc: 0.4907
Epoch 53/100
1070/1070 [==============================] - 0s 461us/step - loss: 1.0492 - acc: 0.4991
Epoch 54/100
1070/1070 [==============================] - 0s 463us/step - loss: 1.0479 - acc: 0.5103
Epoch 55/100
1070/1070 [==============================] - 0s 466us/step - loss: 0.9948 - acc: 0.5065
Epoch 56/100
1070/1070 [==============================] - 0s 462us/step - loss: 1.0215 - acc: 0.5168
Epoch 57/100
1070/1070 [==============================] - 0s 461us/step - loss: 1.0205 - ac

1069/1069 [==============================] - 1s 469us/step - loss: 1.5280 - acc: 0.5529
Epoch 29/100
1069/1069 [==============================] - 0s 464us/step - loss: 1.4278 - acc: 0.5519
Epoch 30/100
1069/1069 [==============================] - 0s 461us/step - loss: 1.4137 - acc: 0.5547
Epoch 31/100
1069/1069 [==============================] - 0s 465us/step - loss: 1.4865 - acc: 0.5491
Epoch 32/100
1069/1069 [==============================] - 1s 468us/step - loss: 1.5297 - acc: 0.5500
Epoch 33/100
1069/1069 [==============================] - 0s 462us/step - loss: 1.4361 - acc: 0.5585
Epoch 34/100
1069/1069 [==============================] - 0s 465us/step - loss: 1.4390 - acc: 0.5613
Epoch 35/100
1069/1069 [==============================] - 0s 467us/step - loss: 1.4350 - acc: 0.5529
Epoch 36/100
1069/1069 [==============================] - 0s 465us/step - loss: 1.2723 - acc: 0.5631
Epoch 37/100
1069/1069 [==============================] - 0s 465us/step - loss: 1.6456 - acc: 0.5463
Epo

1069/1069 [==============================] - 0s 457us/step - loss: 0.6903 - acc: 0.5426
Epoch 90/100
1069/1069 [==============================] - 0s 461us/step - loss: 0.6903 - acc: 0.5463
Epoch 91/100
1069/1069 [==============================] - 1s 471us/step - loss: 0.6907 - acc: 0.5463
Epoch 92/100
1069/1069 [==============================] - 1s 481us/step - loss: 0.6907 - acc: 0.5463
Epoch 93/100
1069/1069 [==============================] - 1s 481us/step - loss: 0.6901 - acc: 0.5332
Epoch 94/100
1069/1069 [==============================] - 1s 479us/step - loss: 0.6905 - acc: 0.5463
Epoch 95/100
1069/1069 [==============================] - 1s 475us/step - loss: 0.6902 - acc: 0.5463
Epoch 96/100
1069/1069 [==============================] - 1s 475us/step - loss: 0.6907 - acc: 0.5463
Epoch 97/100
1069/1069 [==============================] - 1s 476us/step - loss: 0.6910 - acc: 0.5388
Epoch 98/100
1069/1069 [==============================] - 1s 579us/step - loss: 0.6913 - acc: 0.5463
Epo

1604/1604 [==============================] - 1s 532us/step - loss: 0.5150 - acc: 0.7232
Epoch 50/100
1604/1604 [==============================] - 1s 525us/step - loss: 0.5175 - acc: 0.7269
Epoch 51/100
1604/1604 [==============================] - 1s 525us/step - loss: 0.5105 - acc: 0.7319
Epoch 52/100
1604/1604 [==============================] - 1s 519us/step - loss: 0.4990 - acc: 0.7444
Epoch 53/100
1604/1604 [==============================] - 1s 522us/step - loss: 0.5115 - acc: 0.7269
Epoch 54/100
1604/1604 [==============================] - 1s 538us/step - loss: 0.5118 - acc: 0.7288
Epoch 55/100
1604/1604 [==============================] - 1s 535us/step - loss: 0.5048 - acc: 0.7357
Epoch 56/100
1604/1604 [==============================] - 1s 525us/step - loss: 0.5092 - acc: 0.7288
Epoch 57/100
1604/1604 [==============================] - 1s 527us/step - loss: 0.5031 - acc: 0.7375
Epoch 58/100
1604/1604 [==============================] - 1s 519us/step - loss: 0.5136 - acc: 0.7344
Epo

### Tune the Number of Neurons in the Hidden Layer

In [6]:
# Function to create model, required for KerasClassifier
def create_model(neurons=1):
    # create model
    model = Sequential()
    model.add(Dense(neurons, input_dim=8, kernel_initializer='he_uniform', activation='relu', kernel_constraint=maxnorm(3)))
    model.add(Dropout(0.2))
    model.add(Dense(neurons/2, kernel_initializer='he_uniform', activation='relu', kernel_constraint=maxnorm(3)))
    model.add(Dropout(0.2))
    model.add(Dense(1, kernel_initializer='he_uniform', activation='sigmoid'))
          
    # Compile model
    optimizer = SGD(lr=0.2, momentum=0.0)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

# create model
model = KerasClassifier(build_fn=create_model, epochs=100, batch_size=10, verbose=1)
# define the grid search parameters
neurons = [20, 30, 40, 60, 80, 100, 150]
param_grid = dict(neurons=neurons)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1)
grid_result = grid.fit(X, y)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/100
1069/1069 [==============================] - 2s 2ms/step - loss: 0.6941 - acc: 0.5388
Epoch 2/100
1069/1069 [==============================] - 0s 349us/step - loss: 0.6806 - acc: 0.5828
Epoch 3/100
1069/1069 [==============================] - 0s 357us/step - loss: 0.6767 - acc: 0.5753
Epoch 4/100
1069/1069 [==============================] - 0s 336us/step - loss: 0.6744 - acc: 0.5996
Epoch 5/100
1069/1069 [==============================] - 0s 318us/step - loss: 0.6683 - acc: 0.5875
Epoch 6/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.6637 - acc: 0.5837
Epoch 7/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.6389 - acc: 0.6239
Epoch 8/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.6388 - acc: 0.6268
Epoch 9/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.6312 - acc: 0.6324
Epoch 10/100
1069/1069 [==============================] - 0s 321us/step - loss: 0.6189 - acc: 0.6539
E

1069/1069 [==============================] - 0s 307us/step - loss: 0.5648 - acc: 0.6717
Epoch 83/100
1069/1069 [==============================] - 0s 307us/step - loss: 0.6037 - acc: 0.6651
Epoch 84/100
1069/1069 [==============================] - 0s 306us/step - loss: 0.5873 - acc: 0.6791
Epoch 85/100
1069/1069 [==============================] - 0s 308us/step - loss: 0.5777 - acc: 0.6698
Epoch 86/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5710 - acc: 0.6782
Epoch 87/100
1069/1069 [==============================] - 0s 310us/step - loss: 0.5658 - acc: 0.6978
Epoch 88/100
1069/1069 [==============================] - 0s 310us/step - loss: 0.5757 - acc: 0.6838
Epoch 89/100
1069/1069 [==============================] - 0s 309us/step - loss: 0.5586 - acc: 0.6922
Epoch 90/100
1069/1069 [==============================] - 0s 308us/step - loss: 0.5554 - acc: 0.7044
Epoch 91/100
1069/1069 [==============================] - 0s 311us/step - loss: 0.5559 - acc: 0.6969
Epo

1069/1069 [==============================] - 0s 312us/step - loss: 0.5797 - acc: 0.6679
Epoch 63/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5714 - acc: 0.6791
Epoch 64/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.5644 - acc: 0.6838
Epoch 65/100
1069/1069 [==============================] - 0s 311us/step - loss: 0.5701 - acc: 0.6950
Epoch 66/100
1069/1069 [==============================] - 0s 308us/step - loss: 0.5714 - acc: 0.6819
Epoch 67/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5829 - acc: 0.6679
Epoch 68/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5743 - acc: 0.6688
Epoch 69/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5625 - acc: 0.6913
Epoch 70/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5766 - acc: 0.6838
Epoch 71/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5799 - acc: 0.6838
Epo

1070/1070 [==============================] - 0s 318us/step - loss: 0.5538 - acc: 0.7187
Epoch 43/100
1070/1070 [==============================] - 0s 313us/step - loss: 0.5557 - acc: 0.7140
Epoch 44/100
1070/1070 [==============================] - 0s 311us/step - loss: 0.5504 - acc: 0.7168
Epoch 45/100
1070/1070 [==============================] - 0s 312us/step - loss: 0.5466 - acc: 0.7215
Epoch 46/100
1070/1070 [==============================] - 0s 313us/step - loss: 0.5462 - acc: 0.7318
Epoch 47/100
1070/1070 [==============================] - 0s 314us/step - loss: 0.5545 - acc: 0.7131
Epoch 48/100
1070/1070 [==============================] - 0s 321us/step - loss: 0.5561 - acc: 0.7112
Epoch 49/100
1070/1070 [==============================] - 0s 318us/step - loss: 0.5535 - acc: 0.7131
Epoch 50/100
1070/1070 [==============================] - 0s 316us/step - loss: 0.5562 - acc: 0.7112
Epoch 51/100
1070/1070 [==============================] - 0s 312us/step - loss: 0.5512 - acc: 0.7168
Epo

1069/1069 [==============================] - 0s 318us/step - loss: 0.5707 - acc: 0.6801
Epoch 23/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5793 - acc: 0.6698
Epoch 24/100
1069/1069 [==============================] - 0s 320us/step - loss: 0.5736 - acc: 0.6670
Epoch 25/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5766 - acc: 0.6501
Epoch 26/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.5808 - acc: 0.6688
Epoch 27/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5797 - acc: 0.6567
Epoch 28/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5614 - acc: 0.6782
Epoch 29/100
1069/1069 [==============================] - 0s 311us/step - loss: 0.5644 - acc: 0.6726
Epoch 30/100
1069/1069 [==============================] - 0s 317us/step - loss: 0.5645 - acc: 0.6773
Epoch 31/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5770 - acc: 0.6651
Epo

...

1069/1069 [==============================] - 0s 315us/step - loss: 0.5440 - acc: 0.6978
Epoch 47/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5235 - acc: 0.6997
Epoch 48/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.5344 - acc: 0.7109
Epoch 49/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5323 - acc: 0.6988
Epoch 50/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5189 - acc: 0.7128
Epoch 51/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5394 - acc: 0.7007
Epoch 52/100
1069/1069 [==============================] - 0s 317us/step - loss: 0.5383 - acc: 0.7081
Epoch 53/100
1069/1069 [==============================] - 0s 319us/step - loss: 0.5380 - acc: 0.7016
Epoch 54/100
1069/1069 [==============================] - 0s 316us/step - loss: 0.5365 - acc: 0.6960
Epoch 55/100
1069/1069 [==============================] - 0s 310us/step - loss: 0.5375 - acc: 0.7128
Epo

1069/1069 [==============================] - 0s 314us/step - loss: 0.5360 - acc: 0.7100
Epoch 27/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5320 - acc: 0.6988
Epoch 28/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5485 - acc: 0.7007
Epoch 29/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5449 - acc: 0.7147
Epoch 30/100
1069/1069 [==============================] - 0s 314us/step - loss: 0.5358 - acc: 0.7044
Epoch 31/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5391 - acc: 0.7175
Epoch 32/100
1069/1069 [==============================] - 0s 315us/step - loss: 0.5409 - acc: 0.7044
Epoch 33/100
1069/1069 [==============================] - 0s 311us/step - loss: 0.5384 - acc: 0.7044
Epoch 34/100
1069/1069 [==============================] - 0s 313us/step - loss: 0.5341 - acc: 0.7109
Epoch 35/100
1069/1069 [==============================] - 0s 312us/step - loss: 0.5262 - acc: 0.7268
Epo

1070/1070 [==============================] - 0s 312us/step - loss: 0.6107 - acc: 0.6514
Epoch 7/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5952 - acc: 0.6776
Epoch 8/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5874 - acc: 0.6925
Epoch 9/100
1070/1070 [==============================] - 0s 311us/step - loss: 0.5731 - acc: 0.6972
Epoch 10/100
1070/1070 [==============================] - 0s 314us/step - loss: 0.5835 - acc: 0.6850
Epoch 11/100
1070/1070 [==============================] - 0s 311us/step - loss: 0.5541 - acc: 0.7103
Epoch 12/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5733 - acc: 0.6925
Epoch 13/100
1070/1070 [==============================] - 0s 313us/step - loss: 0.5531 - acc: 0.7037
Epoch 14/100
1070/1070 [==============================] - 0s 312us/step - loss: 0.5510 - acc: 0.7140
Epoch 15/100
1070/1070 [==============================] - 0s 311us/step - loss: 0.5618 - acc: 0.7103
Epoch 

1070/1070 [==============================] - 0s 312us/step - loss: 0.5042 - acc: 0.7374
Epoch 88/100
1070/1070 [==============================] - 0s 312us/step - loss: 0.5052 - acc: 0.7467
Epoch 89/100
1070/1070 [==============================] - 0s 309us/step - loss: 0.5182 - acc: 0.7364
Epoch 90/100
1070/1070 [==============================] - 0s 313us/step - loss: 0.5093 - acc: 0.7393
Epoch 91/100
1070/1070 [==============================] - 0s 312us/step - loss: 0.5050 - acc: 0.7346
Epoch 92/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5115 - acc: 0.7551
Epoch 93/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5064 - acc: 0.7336
Epoch 94/100
1070/1070 [==============================] - 0s 309us/step - loss: 0.5098 - acc: 0.7327
Epoch 95/100
1070/1070 [==============================] - 0s 310us/step - loss: 0.5138 - acc: 0.7402
Epoch 96/100
1070/1070 [==============================] - 0s 309us/step - loss: 0.5208 - acc: 0.7411
Epo

1604/1604 [==============================] - 1s 315us/step - loss: 0.5162 - acc: 0.7213
Epoch 68/100
1604/1604 [==============================] - 1s 314us/step - loss: 0.5197 - acc: 0.7307
Epoch 69/100
1604/1604 [==============================] - 1s 317us/step - loss: 0.5250 - acc: 0.7213
Epoch 70/100
1604/1604 [==============================] - 1s 313us/step - loss: 0.5264 - acc: 0.7095
Epoch 71/100
1604/1604 [==============================] - 0s 311us/step - loss: 0.5216 - acc: 0.7226
Epoch 72/100
1604/1604 [==============================] - 1s 312us/step - loss: 0.5233 - acc: 0.7263
Epoch 73/100
1604/1604 [==============================] - 0s 312us/step - loss: 0.5219 - acc: 0.7263
Epoch 74/100
1604/1604 [==============================] - 1s 315us/step - loss: 0.5260 - acc: 0.7294
Epoch 75/100
1604/1604 [==============================] - 1s 317us/step - loss: 0.5317 - acc: 0.7244
Epoch 76/100
1604/1604 [==============================] - 1s 318us/step - loss: 0.5265 - acc: 0.7195
Epo

## Final code

In [106]:
# load train data    
df_train = pd.read_csv('./train_metrics.csv')
target = df_train['target'].values
df_train =df_train.drop(['target'],axis=1)
df_train =df_train.drop(['id'],axis=1)

# Normalize the columns
cols_to_norm = ['normal_dist','normal_intersec', 'fft_dist', 'fft_intersec', 'manhattan_dist', 'minkowski_dist', 'cosine_simil', 'jaccard_simil']
df_train[cols_to_norm] = df_train[cols_to_norm].apply(lambda x: (x - x.min()) / (x.max() - x.min()))

# load test data
df_test = pd.read_csv('./test_metrics.csv')
id_test = df_test['id'].values
df_test =df_test.drop(['id'],axis=1)
df_test =df_test.drop(['target'],axis=1)

# Normalize the columns
cols_to_norm = ['normal_dist','normal_intersec', 'fft_dist', 'fft_intersec', 'manhattan_dist', 'minkowski_dist', 'cosine_simil', 'jaccard_simil']
df_test[cols_to_norm] = df_test[cols_to_norm].apply(lambda x: (x - x.min()) / (x.max() - x.min()))

df_test.head(5)

normal_dist  normal_intersec  fft_dist  fft_intersec  manhattan_dist  \
0     0.511220         0.130671  0.374217      1.000000        0.524694   
1     0.539533         0.196864  0.136421      1.000000        0.177314   
2     0.212919         0.253891  0.175283      0.999443        0.055625   
3     0.295937         0.301961  0.080773      0.640398        0.168869   
4     0.529301         0.163080  0.104705      1.000000        0.140922   

   minkowski_dist  cosine_simil  jaccard_simil  
0        0.586256      0.593750       0.000108  
1        0.221802      0.833333       0.000382  
2        0.053853      0.958333       0.000070  
3        0.229626      0.718750       0.000103  
4        0.190116      0.854167       0.000354

In [107]:
X_train =df_train.values
X_test = df_test.values

scaler=StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test=scaler.fit_transform(X_test)
X_fit, X_eval, y_fit, y_eval= train_test_split(X_train, target, test_size=0.2,random_state=100)

In [108]:
def create_model(dropout_rate=0.0, weight_constraint=0):
    # create model
    model = Sequential()
    model.add(Dense(100, input_dim=8, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(50, kernel_initializer='he_uniform', activation='relu'))
    model.add(Dropout(dropout_rate))
    model.add(Dense(1, kernel_initializer='he_uniform', activation='sigmoid'))

    
    # Compile model
    optimizer = SGD(lr=0.2, momentum=0.0, decay=0.0, nesterov=False)
    model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    return model

# create model
model = create_model()

model.fit(X_fit, y_fit,
              batch_size=10, epochs=200,
              verbose=2,
              validation_data=(X_eval, y_eval))

Train on 1283 samples, validate on 321 samples
Epoch 1/200
 - 2s - loss: 0.5937 - acc: 0.6758 - val_loss: 0.5373 - val_acc: 0.7072
Epoch 2/200
 - 0s - loss: 0.5427 - acc: 0.7124 - val_loss: 0.5024 - val_acc: 0.7539
Epoch 3/200
 - 0s - loss: 0.5132 - acc: 0.7350 - val_loss: 0.5305 - val_acc: 0.7196
Epoch 4/200
 - 0s - loss: 0.5027 - acc: 0.7412 - val_loss: 0.5074 - val_acc: 0.7445
Epoch 5/200
 - 0s - loss: 0.4885 - acc: 0.7451 - val_loss: 0.5619 - val_acc: 0.7040
Epoch 6/200
 - 0s - loss: 0.4984 - acc: 0.7467 - val_loss: 0.5111 - val_acc: 0.7227
Epoch 7/200
 - 0s - loss: 0.4811 - acc: 0.7560 - val_loss: 0.5458 - val_acc: 0.7290
Epoch 8/200
 - 0s - loss: 0.4834 - acc: 0.7405 - val_loss: 0.5014 - val_acc: 0.7570
Epoch 9/200
 - 0s - loss: 0.4706 - acc: 0.7537 - val_loss: 0.5204 - val_acc: 0.7383
Epoch 10/200
 - 0s - loss: 0.4635 - acc: 0.7724 - val_loss: 0.4959 - val_acc: 0.7196
Epoch 11/200
 - 0s - loss: 0.4555 - acc: 0.7779 - val_loss: 0.5106 - val_acc: 0.7508
Epoch 12/200
 - 0s - loss: 

Epoch 97/200
 - 0s - loss: 0.2328 - acc: 0.8971 - val_loss: 0.8739 - val_acc: 0.7134
Epoch 98/200
 - 0s - loss: 0.2450 - acc: 0.8924 - val_loss: 0.8686 - val_acc: 0.7352
Epoch 99/200
 - 0s - loss: 0.2424 - acc: 0.8831 - val_loss: 0.8021 - val_acc: 0.7196
Epoch 100/200
 - 0s - loss: 0.2500 - acc: 0.8831 - val_loss: 0.8019 - val_acc: 0.7321
Epoch 101/200
 - 0s - loss: 0.2473 - acc: 0.8917 - val_loss: 0.8817 - val_acc: 0.7165
Epoch 102/200
 - 0s - loss: 0.2305 - acc: 0.8917 - val_loss: 0.8849 - val_acc: 0.7165
Epoch 103/200
 - 0s - loss: 0.2758 - acc: 0.8706 - val_loss: 0.8230 - val_acc: 0.7695
Epoch 104/200
 - 0s - loss: 0.2801 - acc: 0.8753 - val_loss: 1.0679 - val_acc: 0.6916
Epoch 105/200
 - 0s - loss: 0.2558 - acc: 0.8846 - val_loss: 1.0072 - val_acc: 0.7290
Epoch 106/200
 - 0s - loss: 0.2703 - acc: 0.8815 - val_loss: 0.7383 - val_acc: 0.7445
Epoch 107/200
 - 0s - loss: 0.2391 - acc: 0.8924 - val_loss: 0.8154 - val_acc: 0.7445
Epoch 108/200
 - 0s - loss: 0.2348 - acc: 0.8948 - val_lo

Epoch 193/200
 - 0s - loss: 0.1225 - acc: 0.9462 - val_loss: 1.4434 - val_acc: 0.7196
Epoch 194/200
 - 0s - loss: 0.0938 - acc: 0.9618 - val_loss: 1.5427 - val_acc: 0.7352
Epoch 195/200
 - 0s - loss: 0.0982 - acc: 0.9641 - val_loss: 1.4127 - val_acc: 0.7414
Epoch 196/200
 - 0s - loss: 0.1237 - acc: 0.9532 - val_loss: 1.4611 - val_acc: 0.7040
Epoch 197/200
 - 0s - loss: 0.1807 - acc: 0.9361 - val_loss: 1.5876 - val_acc: 0.7259
Epoch 198/200
 - 0s - loss: 0.3010 - acc: 0.8854 - val_loss: 1.4225 - val_acc: 0.6854
Epoch 199/200
 - 0s - loss: 0.3728 - acc: 0.8714 - val_loss: 1.2309 - val_acc: 0.7103
Epoch 200/200
 - 0s - loss: 0.2306 - acc: 0.9096 - val_loss: 1.0053 - val_acc: 0.7321


In [109]:
score = model.evaluate(X_eval, y_eval,
                           verbose=0)
print('Test score:', score[0])
print('Test accuracy:', score[1])
   
y_pred = model.predict_proba(X_test)[:,0]

('Test score:', 1.0053416311699508)
('Test accuracy:', 0.73208722741433019)


In [103]:
submission = pd.DataFrame({'id': test["id"], 'is_iceberg': y_pred})
output_file = './NN-submission.csv'
submission.to_csv(output_file, index=False)

writting predicted results
